In [1]:
# Calculation of complete reporting rates with program and stock data

%matplotlib inline  
# !pip install matplotlib

import pandas as pd
import numpy as np
import pandas_highcharts.core
from sqlalchemy import create_engine
import psycopg2
import matplotlib.pyplot 

# weird construct - if you don't from * import * you have to use datetime.datetime in commands
from datetime import datetime, date, timedelta

from isoweek import Week

import os

# For exporting excel files using XlsxWriter
from pandas import ExcelWriter
import xlsxwriter

os.environ.setdefault("DJANGO_SETTINGS_MODULE", "IMAM.settings")

from django.conf import settings
from home.management.commands.load_data import rename_cols, assign_state_lga_num

import django
django.setup()

# is this line necessary?
from home.models import Program, Stock, Site

In [2]:
pd.set_option('display.max_rows', 999)
print(pd.get_option("display.max_rows"))

999


In [3]:
pd.set_option('display.max_columns', 999)

In [4]:
# Import Program Data
engine = create_engine(
    'postgresql://{USER}:{PASSWORD}@{HOST}:{PORT}/{NAME}'.format(**settings.DATABASES['default']))
df = pd.read_sql_query("select * from program;", con=engine)


df['year_weeknum'] = zip(df['year'], df['weeknum'])
df['iso_year_weeknum'] = df['year_weeknum'].map(lambda x: Week(x[0], x[1]))

year, week, _ = date.today().isocalendar()
current_week = Week(year, week)

# since how many week this report is about
df['since_x_weeks'] = df['iso_year_weeknum'].map(lambda x: current_week - x)

In [5]:
df.head()

id                          contact_uuid                 urn  \
0  285252771  e56c6b93-7551-494f-9655-6928980179e8  tel:+2347033333861   
1  452570203  800cd521-f444-4e3e-8958-59b0f38b4cc1  tel:+2348036875795   
2  463819625  7be60a60-deb5-476d-8ac8-bcb7fd7c21a9  tel:+2348165573731   
3  452570081  6a1997a5-c2fb-4005-8487-6f0e2b29c874  tel:+2348130001726   
4  445242316  2ea87789-45b4-4336-bb1c-b7ad26b86811  tel:+2347066738595   

                 name groups      siteid                 first_seen  \
0          Turu Umar.   None  3308210004 2016-07-13 21:55:44.352760   
1      Mikailu Laban.   None   212110030 2017-03-30 19:45:23.670070   
2      Mustapha Rawa.   None   821110058 2017-04-28 15:02:57.776168   
3       Sani Ibrahim.   None  2018110036 2017-03-30 19:28:12.381215   
4  Usman Mohd Mande .   None  3306110015 2017-03-16 07:29:59.437968   

                   last_seen  weeknum  role type age_group  beg  amar  tin  \
0 2016-07-13 21:59:32.697931       24  Site   SC     6-59m    0     2    0   
1 2017-03-30 19:55:29.128268       13  Site  OTP     6-59m   51     5    0   
2 2017-04-28 15:12:01.796819       14  Site  OTP     6-59m  201    31    0   
3 2017-03-30 19:50:15.013579       13  Site  OTP     6-59m  241     0    0   
4 2017-03-16 07:41:29.263730        5  Site  OTP     6-59m   69     4    0   

   dcur  dead  defu  dmed  tout confirm siteid_lgt  state_num  lga_num  year  \
0     0     1     1     0     0     Yes       None         33     3308  2016   
1     3     0     1     0     0     Yes       None          2      212  2017   
2    20     0    19     2     0     Yes       None          8      821  2017   
3     0     0     0     0     0     Yes       None         20     2018  2017   
4     3     0     0     0     0     Yes       None         33     3306  2017   

  last_seen_weeknum rep_year_wn rep_weeknum last_seen_dotw last_seen_hour  \
0              None        None        None           None           None   
1              None        None        None           None           None   
2              None        None        None           None           None   
3              None        None        None           None           None   
4              None        None        None           None           None   

  year_weeknum iso_rep_year_wn iso_year_weeknum  iso_diff  since_x_weeks  
0   (2016, 24)            None       (2016, 24)        -4             50  
1   (2017, 13)            None       (2017, 13)         0              9  
2   (2017, 14)            None       (2017, 14)        -3              8  
3   (2017, 13)            None       (2017, 13)         0              9  
4    (2017, 5)            None        (2017, 5)        -6             17

In [6]:
# Active / Inactive Sites
# Integrate this into import program

# See below for weekly reminders

active_sites = df.query('since_x_weeks<=8')\
                .query('siteid>101110001')\
                .groupby(['siteid', 'type'])['siteid']\
                .unique()
active_sites

siteid      type
201110007   OTP      [201110007]
201110009   OTP      [201110009]
201110021   OTP      [201110021]
202110019   OTP      [202110019]
202110021   OTP      [202110021]
202110035   OTP      [202110035]
202110068   OTP      [202110068]
202610001   SC       [202610001]
203110002   OTP      [203110002]
203110037   OTP      [203110037]
203110038   OTP      [203110038]
203110043   OTP      [203110043]
203110053   OTP      [203110053]
204110006   OTP      [204110006]
204110014   OTP      [204110014]
204110026   OTP      [204110026]
204110029   OTP      [204110029]
204110035   OTP      [204110035]
205110039   OTP      [205110039]
206110004   OTP      [206110004]
206110011   OTP      [206110011]
206110020   OTP      [206110020]
206110032   OTP      [206110032]
206110034   OTP      [206110034]
207110055   OTP      [207110055]
207110082   OTP      [207110082]
207110088   OTP      [207110088]
207110089   OTP      [207110089]
207140015   OTP      [207140015]
208110006   OTP      [2081

In [7]:
all_sites = df.query('siteid>101110001').groupby(['siteid', 'type'])['siteid'].unique()
all_sites

siteid      type
201110007   OTP      [201110007]
201110009   OTP      [201110009]
201110021   OTP      [201110021]
201110026   OTP      [201110026]
201110029   OTP      [201110029]
201410014   OTP      [201410014]
202110019   OTP      [202110019]
202110021   OTP      [202110021]
202110027   OTP      [202110027]
202110035   OTP      [202110035]
202110068   OTP      [202110068]
202610001   SC       [202610001]
203110002   OTP      [203110002]
203110037   OTP      [203110037]
203110038   OTP      [203110038]
203110043   OTP      [203110043]
203110053   OTP      [203110053]
204110006   OTP      [204110006]
204110014   OTP      [204110014]
204110026   OTP      [204110026]
204110029   OTP      [204110029]
204110035   OTP      [204110035]
205110025   OTP      [205110025]
205110030   OTP      [205110030]
205110039   OTP      [205110039]
206110004   OTP      [206110004]
206110011   OTP      [206110011]
206110020   OTP      [206110020]
206110032   OTP      [206110032]
206110034   OTP      [2061

In [8]:
a = all_sites.to_frame()
a

siteid
siteid     type              
201110007  OTP    [201110007]
201110009  OTP    [201110009]
201110021  OTP    [201110021]
201110026  OTP    [201110026]
201110029  OTP    [201110029]
201410014  OTP    [201410014]
202110019  OTP    [202110019]
202110021  OTP    [202110021]
202110027  OTP    [202110027]
202110035  OTP    [202110035]
202110068  OTP    [202110068]
202610001  SC     [202610001]
203110002  OTP    [203110002]
203110037  OTP    [203110037]
203110038  OTP    [203110038]
203110043  OTP    [203110043]
203110053  OTP    [203110053]
204110006  OTP    [204110006]
204110014  OTP    [204110014]
204110026  OTP    [204110026]
204110029  OTP    [204110029]
204110035  OTP    [204110035]
205110025  OTP    [205110025]
205110030  OTP    [205110030]
205110039  OTP    [205110039]
206110004  OTP    [206110004]
206110011  OTP    [206110011]
206110020  OTP    [206110020]
206110032  OTP    [206110032]
206110034  OTP    [206110034]
207110015  OTP    [207110015]
207110055  OTP    [207110055]
207110082  OTP    [207110082]
207110088  OTP    [207110088]
207110089  OTP    [207110089]
207140015  OTP    [207140015]
208110006  OTP    [208110006]
208110021  OTP    [208110021]
208110024  OTP    [208110024]
208110029  OTP    [208110029]
208110033  OTP    [208110033]
209110005  OTP    [209110005]
209110009  OTP    [209110009]
209110011  OTP    [209110011]
209110019  OTP    [209110019]
209110025  OTP    [209110025]
210110016  OTP    [210110016]
210110042  OTP    [210110042]
210110054  OTP    [210110054]
210611020  OTP    [210611020]
211110015  OTP    [211110015]
211110029  OTP    [211110029]
211110047  OTP    [211110047]
212110003  OTP    [212110003]
212110010  OTP    [212110010]
212110030  OTP    [212110030]
212110045  OTP    [212110045]
212110049  OTP    [212110049]
213110006  OTP    [213110006]
213110012  OTP    [213110012]
213110043  OTP    [213110043]
213110055  OTP    [213110055]
213110059  OTP    [213110059]
214110013  OTP    [214110013]
214110039  OTP    [214110039]
214110044  OTP    [214110044]
215110001  OTP    [215110001]
215110017  OTP    [215110017]
215110024  OTP    [215110024]
215110046  OTP    [215110046]
216110001  OTP    [216110001]
216110010  OTP    [216110010]
216110015  OTP    [216110015]
216110032  OTP    [216110032]
216110035  OTP    [216110035]
217110006  OTP    [217110006]
217110028  OTP    [217110028]
217110030  OTP    [217110030]
217110037  OTP    [217110037]
217110038  OTP    [217110038]
218110009  OTP    [218110009]
218110025  OTP    [218110025]
218110030  OTP    [218110030]
218110053  OTP    [218110053]
218110063  OTP    [218110063]
219110004  OTP    [219110004]
219110016  OTP    [219110016]
219110020  OTP    [219110020]
220110012  OTP    [220110012]
220110023  OTP    [220110023]
220110044  OTP    [220110044]
220110045  OTP    [220110045]
221110007  OTP    [221110007]
221110009  OTP    [221110009]
221110012  OTP    [221110012]
221110013  OTP    [221110013]
221110027  OTP    [221110027]
350110031  OTP    [350110031]
350911013  OTP    [350911013]
504110010  OTP    [504110010]
504110020  OTP    [504110020]
504110027  OTP    [504110027]
504110033  OTP    [504110033]
504110035  OTP    [504110035]
504210004  SC     [504210004]
512110003  OTP    [512110003]
512110020  OTP    [512110020]
512110027  OTP    [512110027]
512110040  OTP    [512110040]
512110044  OTP    [512110044]
512210018  SC     [512210018]
513110003  OTP    [513110003]
513110017  OTP    [513110017]
513110021  OTP    [513110021]
513110028  OTP    [513110028]
513110042  OTP    [513110042]
513210023  SC     [513210023]
802110002  OTP    [802110002]
802110007  OTP    [802110007]
802110010  OTP    [802110010]
802110022  OTP    [802110022]
802110024  OTP    [802110024]
802210001  SC     [802210001]
803210010  OTP    [803210010]
803210026  OTP    [803210026]
804110001  OTP    [804110001]
804110003  OTP    [804110003]
804110005  OTP    [804110005]
804110007  OTP    [804110007]
804110009  OTP    [804110009]
804110011  OTP    [804110011]
804110015  OTP    [804110015]
804

In [9]:
a = a.drop('siteid', axis=1).reset_index()
a

siteid type
0     201110007  OTP
1     201110009  OTP
2     201110021  OTP
3     201110026  OTP
4     201110029  OTP
5     201410014  OTP
6     202110019  OTP
7     202110021  OTP
8     202110027  OTP
9     202110035  OTP
10    202110068  OTP
11    202610001   SC
12    203110002  OTP
13    203110037  OTP
14    203110038  OTP
15    203110043  OTP
16    203110053  OTP
17    204110006  OTP
18    204110014  OTP
19    204110026  OTP
20    204110029  OTP
21    204110035  OTP
22    205110025  OTP
23    205110030  OTP
24    205110039  OTP
25    206110004  OTP
26    206110011  OTP
27    206110020  OTP
28    206110032  OTP
29    206110034  OTP
30    207110015  OTP
31    207110055  OTP
32    207110082  OTP
33    207110088  OTP
34    207110089  OTP
35    207140015  OTP
36    208110006  OTP
37    208110021  OTP
38    208110024  OTP
39    208110029  OTP
40    208110033  OTP
41    209110005  OTP
42    209110009  OTP
43    209110011  OTP
44    209110019  OTP
45    209110025  OTP
46    210110016  OTP
47    210110042  OTP
48    210110054  OTP
49    210611020  OTP
50    211110015  OTP
51    211110029  OTP
52    211110047  OTP
53    212110003  OTP
54    212110010  OTP
55    212110030  OTP
56    212110045  OTP
57    212110049  OTP
58    213110006  OTP
59    213110012  OTP
60    213110043  OTP
61    213110055  OTP
62    213110059  OTP
63    214110013  OTP
64    214110039  OTP
65    214110044  OTP
66    215110001  OTP
67    215110017  OTP
68    215110024  OTP
69    215110046  OTP
70    216110001  OTP
71    216110010  OTP
72    216110015  OTP
73    216110032  OTP
74    216110035  OTP
75    217110006  OTP
76    217110028  OTP
77    217110030  OTP
78    217110037  OTP
79    217110038  OTP
80    218110009  OTP
81    218110025  OTP
82    218110030  OTP
83    218110053  OTP
84    218110063  OTP
85    219110004  OTP
86    219110016  OTP
87    219110020  OTP
88    220110012  OTP
89    220110023  OTP
90    220110044  OTP
91    220110045  OTP
92    221110007  OTP
93    221110009  OTP
94    221110012  OTP
95    221110013  OTP
96    221110027  OTP
97    350110031  OTP
98    350911013  OTP
99    504110010  OTP
100   504110020  OTP
101   504110027  OTP
102   504110033  OTP
103   504110035  OTP
104   504210004   SC
105   512110003  OTP
106   512110020  OTP
107   512110027  OTP
108   512110040  OTP
109   512110044  OTP
110   512210018   SC
111   513110003  OTP
112   513110017  OTP
113   513110021  OTP
114   513110028  OTP
115   513110042  OTP
116   513210023   SC
117   802110002  OTP
118   802110007  OTP
119   802110010  OTP
120   802110022  OTP
121   802110024  OTP
122   802210001   SC
123   803210010  OTP
124   803210026  OTP
125   804110001  OTP
126   804110003  OTP
127   804110005  OTP
128   804110007  OTP
129   804110009  OTP
130   804110011  OTP
131   804110015  OTP
132   804110016  OTP
133   804110019  OTP
134   804110023  OTP
135   804110025  OTP
136   804210002   SC
137   805110005  OTP
138   805110006  OTP
139   805110007  OTP
140   805110010  OTP
141   805110012  OTP
142   805110013  OTP
143   805110018  OTP
144   805110019  OTP
145   805110020  OTP
146   805110021  OTP
147   805110022  OTP
148   805120003  OTP
149   805210001   SC
150   806110002  OTP
151   806110002   SC
152   806110004  OTP
153   806110012  OTP
154   806110018  OTP
155   807110003  OTP
156   807110008  OTP
157   807110017  OTP
158   807110018  OTP
159   807210007  OTP
160   809110001  OTP
161   809110008  OTP
162   811110002  OTP
163   811110019  OTP
164   811110033  OTP
165   812110001  OTP
166   812110005  OTP
167   812110006  OTP
168   812110015  OTP
169   812110016  OTP
170   812110019  OTP
171   812120009  OTP
172   812210021  OTP
173   812210022  OTP
174   813110001  OTP
175   813110003  OTP
176   813110006  OTP
177   813110007  OTP
178   813110011  OTP
179   813110012  OTP
180   813110016  OTP
181   813110017  OTP
182   813110020  OTP
183   813110023  OTP
184   813110024  OTP
185   813110025  OTP
186   813110026  OTP
187   813110027  OTP
188   813110028  OTP
189   813110029  OT

In [10]:
b = active_sites.to_frame().drop('siteid', axis=1).reset_index()
b

siteid type
0     201110007  OTP
1     201110009  OTP
2     201110021  OTP
3     202110019  OTP
4     202110021  OTP
5     202110035  OTP
6     202110068  OTP
7     202610001   SC
8     203110002  OTP
9     203110037  OTP
10    203110038  OTP
11    203110043  OTP
12    203110053  OTP
13    204110006  OTP
14    204110014  OTP
15    204110026  OTP
16    204110029  OTP
17    204110035  OTP
18    205110039  OTP
19    206110004  OTP
20    206110011  OTP
21    206110020  OTP
22    206110032  OTP
23    206110034  OTP
24    207110055  OTP
25    207110082  OTP
26    207110088  OTP
27    207110089  OTP
28    207140015  OTP
29    208110006  OTP
30    208110021  OTP
31    208110024  OTP
32    208110029  OTP
33    208110033  OTP
34    209110005  OTP
35    209110009  OTP
36    209110011  OTP
37    209110019  OTP
38    209110025  OTP
39    210110016  OTP
40    210110054  OTP
41    211110015  OTP
42    211110029  OTP
43    211110047  OTP
44    212110003  OTP
45    212110010  OTP
46    212110030  OTP
47    212110045  OTP
48    212110049  OTP
49    213110006  OTP
50    213110012  OTP
51    213110043  OTP
52    213110055  OTP
53    213110059  OTP
54    215110001  OTP
55    215110024  OTP
56    215110046  OTP
57    216110001  OTP
58    216110032  OTP
59    217110006  OTP
60    217110028  OTP
61    217110030  OTP
62    217110037  OTP
63    217110038  OTP
64    218110025  OTP
65    218110030  OTP
66    218110063  OTP
67    219110020  OTP
68    220110012  OTP
69    220110023  OTP
70    220110044  OTP
71    220110045  OTP
72    221110009  OTP
73    221110012  OTP
74    221110013  OTP
75    221110027  OTP
76    350110031  OTP
77    504110010  OTP
78    504110020  OTP
79    504110027  OTP
80    504110033  OTP
81    504110035  OTP
82    504210004   SC
83    512110003  OTP
84    512110020  OTP
85    512110027  OTP
86    512110040  OTP
87    512110044  OTP
88    512210018   SC
89    513110003  OTP
90    513110017  OTP
91    513110021  OTP
92    513110028  OTP
93    513110042  OTP
94    513210023   SC
95    802110002  OTP
96    802110007  OTP
97    802110010  OTP
98    802110022  OTP
99    802110024  OTP
100   802210001   SC
101   803210010  OTP
102   803210026  OTP
103   804110001  OTP
104   804110003  OTP
105   804110007  OTP
106   804110011  OTP
107   804110015  OTP
108   804110016  OTP
109   804110023  OTP
110   804110025  OTP
111   804210002   SC
112   805110005  OTP
113   805110006  OTP
114   805110007  OTP
115   805110010  OTP
116   805110012  OTP
117   805110013  OTP
118   805110018  OTP
119   805110019  OTP
120   805110020  OTP
121   805110021  OTP
122   805110022  OTP
123   805120003  OTP
124   805210001   SC
125   806110002   SC
126   806110004  OTP
127   806110012  OTP
128   806110018  OTP
129   807110003  OTP
130   807110008  OTP
131   807110017  OTP
132   807110018  OTP
133   807210007  OTP
134   809110001  OTP
135   809110008  OTP
136   811110002  OTP
137   811110019  OTP
138   811110033  OTP
139   812110001  OTP
140   812110005  OTP
141   812110006  OTP
142   812110015  OTP
143   812110016  OTP
144   812110019  OTP
145   812120009  OTP
146   812210021  OTP
147   812210022  OTP
148   813110001  OTP
149   813110003  OTP
150   813110007  OTP
151   813110011  OTP
152   813110012  OTP
153   813110017  OTP
154   813110024  OTP
155   813110025  OTP
156   813110026  OTP
157   813110027  OTP
158   813110029  OTP
159   813110030  OTP
160   813110031  OTP
161   813110032  OTP
162   813110033  OTP
163   813110034  OTP
164   813110035  OTP
165   813110036  OTP
166   813110037  OTP
167   813110038  OTP
168   814110002  OTP
169   814110004  OTP
170   816110001  OTP
171   816110003  OTP
172   816110004  OTP
173   816110005  OTP
174   816110007  OTP
175   816110008  OTP
176   816110029  OTP
177   816110030  OTP
178   816110031  OTP
179   816110034  OTP
180   816110035  OTP
181   816110036  OTP
182   818110001  OTP
183   818110004  OTP
184   818110005  OTP
185   818110006  OTP
186   818110007  OTP
187   818110008  OTP
188   818110010  OTP
189   818110012  OT

In [11]:
zip(a['siteid'], a['type'])

[(201110007, u'OTP'),
 (201110009, u'OTP'),
 (201110021, u'OTP'),
 (201110026, u'OTP'),
 (201110029, u'OTP'),
 (201410014, u'OTP'),
 (202110019, u'OTP'),
 (202110021, u'OTP'),
 (202110027, u'OTP'),
 (202110035, u'OTP'),
 (202110068, u'OTP'),
 (202610001, u'SC'),
 (203110002, u'OTP'),
 (203110037, u'OTP'),
 (203110038, u'OTP'),
 (203110043, u'OTP'),
 (203110053, u'OTP'),
 (204110006, u'OTP'),
 (204110014, u'OTP'),
 (204110026, u'OTP'),
 (204110029, u'OTP'),
 (204110035, u'OTP'),
 (205110025, u'OTP'),
 (205110030, u'OTP'),
 (205110039, u'OTP'),
 (206110004, u'OTP'),
 (206110011, u'OTP'),
 (206110020, u'OTP'),
 (206110032, u'OTP'),
 (206110034, u'OTP'),
 (207110015, u'OTP'),
 (207110055, u'OTP'),
 (207110082, u'OTP'),
 (207110088, u'OTP'),
 (207110089, u'OTP'),
 (207140015, u'OTP'),
 (208110006, u'OTP'),
 (208110021, u'OTP'),
 (208110024, u'OTP'),
 (208110029, u'OTP'),
 (208110033, u'OTP'),
 (209110005, u'OTP'),
 (209110009, u'OTP'),
 (209110011, u'OTP'),
 (209110019, u'OTP'),
 (209110025

In [12]:
len(set(zip(a['siteid'], a['type'])) - set(zip(b['siteid'], b['type'])))

113

In [18]:
a.values

array([[201110007, u'OTP'],
       [201110009, u'OTP'],
       [201110021, u'OTP'],
       ..., 
       [3613110044, u'OTP'],
       [3613110051, u'OTP'],
       [3613210035, u'SC']], dtype=object)

In [15]:
# REMOVE one df from df
# THis was to remove inactive sites from df of all sites

# Supposed fastest np method
b[b.apply(lambda x: x.values not in a.values, axis=1)]

0      False
1      False
2      False
3      False
4      False
5      False
6      False
7      False
8      False
9      False
10     False
11     False
12     False
13     False
14     False
15     False
16     False
17     False
18     False
19     False
20     False
21     False
22     False
23     False
24     False
25     False
26     False
27     False
28     False
29     False
30     False
31     False
32     False
33     False
34     False
35     False
36     False
37     False
38     False
39     False
40     False
41     False
42     False
43     False
44     False
45     False
46     False
47     False
48     False
49     False
50     False
51     False
52     False
53     False
54     False
55     False
56     False
57     False
58     False
59     False
60     False
61     False
62     False
63     False
64     False
65     False
66     False
67     False
68     False
69     False
70     False
71     False
72     False
73     False
74     False
75     False
76     False

In [14]:
pd.concat([a,b,b]).drop_duplicates(keep=False)

siteid type
3     201110026  OTP
4     201110029  OTP
5     201410014  OTP
8     202110027  OTP
22    205110025  OTP
23    205110030  OTP
30    207110015  OTP
47    210110042  OTP
49    210611020  OTP
63    214110013  OTP
64    214110039  OTP
65    214110044  OTP
67    215110017  OTP
71    216110010  OTP
72    216110015  OTP
74    216110035  OTP
80    218110009  OTP
83    218110053  OTP
85    219110004  OTP
86    219110016  OTP
92    221110007  OTP
98    350911013  OTP
127   804110005  OTP
129   804110009  OTP
133   804110019  OTP
150   806110002  OTP
176   813110006  OTP
180   813110016  OTP
182   813110020  OTP
183   813110023  OTP
188   813110028  OTP
207   816110013  OTP
208   816110022  OTP
209   816110028  OTP
226   818118813  OTP
237   821110007  OTP
240   821110012  OTP
245   821110029  OTP
275   824110004  OTP
276   824110025  OTP
277   825110005  OTP
284   827110010  OTP
285   827110012  OTP
303  1609110022  OTP
337  1712110010  OTP
346  1714210021   SC
355  1717110010   SC
357  1717110018  OTP
366  1720110005  OTP
384  1805110032  OTP
385  1805110033  OTP
386  1805110047  OTP
388  1807210001  OTP
397  1818210001   SC
422  1928110011   SC
440  2001110004   SC
459  2004110027  OTP
468  2007110006  OTP
475  2010110007  OTP
486  2011110025  OTP
495  2011120017  OTP
507  2016110031   SC
529  2026210001   SC
542  2034110001   SC
544  2034110006  OTP
556  2102110001  OTP
566  2103210004   SC
574  2104110012  OTP
580  2105110015  OTP
604  2108210020   SC
607  2109110016  OTP
616  2111110011  OTP
630  2114110007  OTP
637  2115110016  OTP
638  2115110017  OTP
642  2117110009  OTP
649  2118110014  OTP
652  2119110001  OTP
655  2119110014  OTP
664  3301210002   SC
713  3321310007   SC
720  3501110011  OTP
722  3501110014  OTP
743  3503110017  OTP
745  3503110019  OTP
746  3503110020  OTP
748  3503210022   SC
759  3505110016  OTP
760  3505110017  OTP
766  3505110037  OTP
792  3508110029  OTP
793  3508110034  OTP
794  3509110003  OTP
801  3509110028  OTP
805  3510110004  OTP
813  3510110019  OTP
819  3511110018   SC
826  3512110028  OTP
827  3512110031  OTP
837  3513110016  OTP
840  3513310012   SC
853  3514110032  OTP
856  3515110002  OTP
857  3515110005  OTP
858  3515110007  OTP
861  3516110002  OTP
864  3516210018  OTP
865  3516210018   SC
888  3603110037  OTP
901  3607210063   SC
916  3611110031  OTP
918  3611210024   SC
925  3613210035   SC

In [14]:
[x for x in all_sites]

[array([201110007]),
 array([201110009]),
 array([201110021]),
 array([201110026]),
 array([201110029]),
 array([201410014]),
 array([202110019]),
 array([202110021]),
 array([202110027]),
 array([202110035]),
 array([202110068]),
 array([202610001]),
 array([203110002]),
 array([203110037]),
 array([203110038]),
 array([203110043]),
 array([203110053]),
 array([204110006]),
 array([204110014]),
 array([204110026]),
 array([204110029]),
 array([204110035]),
 array([205110025]),
 array([205110030]),
 array([205110039]),
 array([206110004]),
 array([206110011]),
 array([206110020]),
 array([206110032]),
 array([206110034]),
 array([207110015]),
 array([207110055]),
 array([207110082]),
 array([207110088]),
 array([207110089]),
 array([207140015]),
 array([208110006]),
 array([208110021]),
 array([208110024]),
 array([208110029]),
 array([208110033]),
 array([209110005]),
 array([209110009]),
 array([209110011]),
 array([209110019]),
 array([209110025]),
 array([210110016]),
 array([21011

In [19]:
len(set([x[0] for x in all_sites]) - set([x[0] for x in active_sites]))

102

In [20]:
len(active_sites)

813

In [21]:
len(all_sites) - len(active_sites)

113

In [22]:
len(set([x[0] for x in all_sites]))

901

In [19]:
# Weekly reminders

# df.query('since_x_weeks>0')\
# REMOVE all reports from current week

# .query('since_x_weeks<=8')\
# REMOVE all reports from more than 8 weeks ago

# .query('siteid>101110001')\
# REMOVE siteids that are test data

# .groupby(['siteid', 'type'])['weeknum']\
# GROUPBY week number over all siteids and site types

# .unique()
# KEEP only one report per site

# .map(lambda x: list(sorted(set(range(week - 8, week)) - set(x))))\
# ITERATE over the set of all possible weeknumbers to remove the weeknumbers of received reports to 
# PRODUCE list of weeknumbers of missing reports. 

# .to_frame()
# SET output to dataframe


In [23]:
week

22

In [24]:
# Calculate missing reports
promiss = df.query('since_x_weeks>0')\
        .query('since_x_weeks<=8')\
        .query('siteid>101110001')\
        .groupby(['siteid', 'type'])['weeknum']\
        .unique()\
        .map(lambda x: list(sorted(set(range(week - 8, week)) - set(x))))\
        .to_frame()

In [28]:
promiss.reset_index().sort_values(by='siteid').head()

siteid type               weeknum
0  201110007  OTP          [19, 20, 21]
1  201110009  OTP                    []
2  201110021  OTP                    []
3  202110019  OTP  [14, 18, 19, 20, 21]
4  202110021  OTP                  [21]

In [29]:
promiss = promiss.reset_index()
promiss = promiss.rename(index=str, columns={"weeknum": "missing_program"})


In [30]:
promiss['missing_program_len'] = promiss.missing_program.map(lambda x:(len(x)))

In [31]:
# Drop rows where missing_program is null
print promiss.missing_program[0]
print promiss.missing_program[0] == True
print promiss.missing_program[0] == False
# Length of list
print len(promiss.missing_program[0])
# Use length to identify rows with no missing data

[19, 20, 21]
False
False
3


In [16]:
# Error in ProMiss

# weeknumber 20 - missing program stock numbers were 16, 17
# siteID 2034110018

In [32]:
# Create missing stock reports
stock = pd.read_sql_query("select * from stock;", con=engine)

In [33]:
stock['year_weeknum'] = zip(stock['year'], stock['weeknum'])
stock['iso_year_weeknum'] = stock['year_weeknum'].map(lambda x: Week(x[0], x[1]))

year, week, _ = date.today().isocalendar()
current_week = Week(year, week)

# since how many week this report is about
stock['since_x_weeks'] = stock['iso_year_weeknum'].map(lambda x: current_week - x)

In [34]:
# stock missing reports
stomiss = stock.query('since_x_weeks>0')\
        .query('since_x_weeks<=8')\
        .query('siteid>101110001')\
        .groupby(['siteid', 'type'])['weeknum']\
        .unique()\
        .map(lambda x: list(sorted(set(range(week - 8, week)) - set(x))))\
        .to_frame()

stomiss

weeknum
siteid     type                              
201110007  OTP                   [19, 20, 21]
201110009  OTP                             []
201110021  OTP                             []
202110019  OTP           [14, 18, 19, 20, 21]
202110021  OTP                           [21]
202110035  OTP                           [21]
202110068  OTP                           [21]
202610001  SC                    [19, 20, 21]
203110002  OTP                             []
203110037  OTP                             []
203110038  OTP                             []
203110043  OTP                             []
203110053  OTP                   [19, 20, 21]
204110006  OTP                             []
204110014  OTP           [17, 18, 19, 20, 21]
204110026  OTP                       [20, 21]
204110029  OTP                       [20, 21]
204110035  OTP           [17, 18, 19, 20, 21]
205110039  OTP           [17, 18, 19, 20, 21]
206110004  OTP                             []
206110011  OTP                             []
206110020  OTP                             []
206110032  OTP                             []
206110034  OTP                             []
207110055  OTP                             []
207110082  OTP               [18, 19, 20, 21]
207110089  OTP                           [21]
208110006  OTP           [17, 18, 19, 20, 21]
208110021  OTP                       [19, 21]
208110024  OTP                             []
208110029  OTP                           [17]
208110033  OTP                           [21]
209110005  OTP               [18, 19, 20, 21]
209110009  OTP                   [19, 20, 21]
209110011  OTP           [17, 18, 19, 20, 21]
209110019  OTP                             []
209110025  OTP                   [19, 20, 21]
210110016  OTP                   [18, 19, 21]
210110054  OTP                             []
211110015  OTP                             []
211110029  OTP                             []
211110047  OTP           [17, 18, 19, 20, 21]
212110003  OTP                             []
212110010  OTP                           [21]
212110030  OTP                             []
212110045  OTP                             []
212110049  OTP                           [21]
213110006  OTP       [16, 17, 18, 19, 20, 21]
213110012  OTP                             []
213110043  OTP                           [21]
213110055  OTP                       [18, 21]
213110059  OTP                       [20, 21]
215110001  OTP                           [21]
215110024  OTP                             []
215110046  OTP                       [17, 21]
216110001  OTP                       [20, 21]
216110032  OTP           [17, 18, 19, 20, 21]
217110006  OTP                             []
217110028  OTP                             []
217110030  OTP                             []
217110037  OTP                             []
217110038  OTP                             []
218110025  OTP               [18, 19, 20, 21]
218110030  OTP                       [18, 21]
218110063  OTP                             []
219110020  OTP                           [21]
220110012  OTP                             []
220110023  OTP                       [20, 21]
220110044  OTP                             []
220110045  OTP                             []
221110009  OTP                             []
221110012  OTP                             []
221110013  OTP                           [21]
221110027  OTP                           [21]
504110010  OTP                             []
504110020  OTP               [18, 19, 20, 21]
504110027  OTP                             []
504110033  OTP                           [21]
504110035  OTP                             []
504210004  SC                            [21]
507110006  OTP   [15, 16, 17, 18, 19, 20, 21]
512110003  OTP                           [21]
512110027  OTP               [18, 19, 20, 21]
512110040  OTP                             []
512110044  OTP                             []
512210018  SC                    [19

In [35]:
stomiss = stomiss.reset_index()
stomiss = stomiss.rename(index = str, columns = {"weeknum": "missing_stock"})


In [36]:
stomiss['missing_stock_len'] = stomiss.missing_stock.map(lambda x:(len(x)))


In [37]:
stomiss

siteid type                 missing_stock  missing_stock_len
0     201110007  OTP                  [19, 20, 21]                  3
1     201110009  OTP                            []                  0
2     201110021  OTP                            []                  0
3     202110019  OTP          [14, 18, 19, 20, 21]                  5
4     202110021  OTP                          [21]                  1
5     202110035  OTP                          [21]                  1
6     202110068  OTP                          [21]                  1
7     202610001   SC                  [19, 20, 21]                  3
8     203110002  OTP                            []                  0
9     203110037  OTP                            []                  0
10    203110038  OTP                            []                  0
11    203110043  OTP                            []                  0
12    203110053  OTP                  [19, 20, 21]                  3
13    204110006  OTP                            []                  0
14    204110014  OTP          [17, 18, 19, 20, 21]                  5
15    204110026  OTP                      [20, 21]                  2
16    204110029  OTP                      [20, 21]                  2
17    204110035  OTP          [17, 18, 19, 20, 21]                  5
18    205110039  OTP          [17, 18, 19, 20, 21]                  5
19    206110004  OTP                            []                  0
20    206110011  OTP                            []                  0
21    206110020  OTP                            []                  0
22    206110032  OTP                            []                  0
23    206110034  OTP                            []                  0
24    207110055  OTP                            []                  0
25    207110082  OTP              [18, 19, 20, 21]                  4
26    207110089  OTP                          [21]                  1
27    208110006  OTP          [17, 18, 19, 20, 21]                  5
28    208110021  OTP                      [19, 21]                  2
29    208110024  OTP                            []                  0
30    208110029  OTP                          [17]                  1
31    208110033  OTP                          [21]                  1
32    209110005  OTP              [18, 19, 20, 21]                  4
33    209110009  OTP                  [19, 20, 21]                  3
34    209110011  OTP          [17, 18, 19, 20, 21]                  5
35    209110019  OTP                            []                  0
36    209110025  OTP                  [19, 20, 21]                  3
37    210110016  OTP                  [18, 19, 21]                  3
38    210110054  OTP                            []                  0
39    211110015  OTP                            []                  0
40    211110029  OTP                            []                  0
41    211110047  OTP          [17, 18, 19, 20, 21]                  5
42    212110003  OTP                            []                  0
43    212110010  OTP                          [21]                  1
44    212110030  OTP                            []                  0
45    212110045  OTP                            []                  0
46    212110049  OTP                          [21]                  1
47    213110006  OTP      [16, 17, 18, 19, 20, 21]                  6
48    213110012  OTP                            []                  0
49    213110043  OTP                          [21]                  1
50    213110055  OTP                      [18, 21]                  2
51    213110059  OTP                      [20, 21]                  2
52    215110001  OTP                          [21]                  1
53    215110024  OTP                            []                  0
54    215110046  OTP                      [17, 21]                  2
55    216110001  OTP                      [20, 21]                  2
56    216110032  OT

In [38]:
# Merge program and stock together

missing_reports = pd.merge(promiss, stomiss, left_on=['siteid', 'type'],\
                           right_on=['siteid', 'type'], how='outer', sort=False)

In [24]:
# replace NaN with range current week - 1 to week - 8
range(1, 9)

[1, 2, 3, 4, 5, 6, 7, 8]

In [25]:
print current_week
print current_week - 1

2017W20
2017W19


In [26]:
previous_week = (current_week - 1)
previous_week.week

19

In [39]:
# create list of weeks that reports are expected
target_weeks = []
for i in range(1, 9):
    target_weeks.append((current_week - i).week)
    
target_weeks = list(reversed(target_weeks))
target_weeks

[14, 15, 16, 17, 18, 19, 20, 21]

In [28]:
np.nan == np.nan

False

In [40]:
# missing_reports.replace({np.nan: target_weeks})
# np.where((missing_reports['missing_program'] != missing_reports['missing_program']), [target_weeks, missing_reports['missing_program']])

missing_reports['missing_program'] = missing_reports['missing_program'].map(lambda x: x if x == x else target_weeks)
missing_reports['missing_stock'] = missing_reports['missing_stock'].map(lambda x: x if x == x else target_weeks)

missing_reports['missing_program_len'] = missing_reports.missing_program.map(lambda x:(len(x)))
missing_reports['missing_stock_len'] = missing_reports.missing_stock.map(lambda x:(len(x)))


missing_reports

siteid type                   missing_program  missing_program_len  \
0     201110007  OTP                      [19, 20, 21]                    3   
1     201110009  OTP                                []                    0   
2     201110021  OTP                                []                    0   
3     202110019  OTP              [14, 18, 19, 20, 21]                    5   
4     202110021  OTP                              [21]                    1   
5     202110035  OTP                              [21]                    1   
6     202110068  OTP                              [21]                    1   
7     202610001   SC                      [19, 20, 21]                    3   
8     203110002  OTP                                []                    0   
9     203110037  OTP                                []                    0   
10    203110038  OTP                                []                    0   
11    203110043  OTP                                []                    0   
12    203110053  OTP                      [19, 20, 21]                    3   
13    204110006  OTP                                []                    0   
14    204110014  OTP              [17, 18, 19, 20, 21]                    5   
15    204110026  OTP                          [20, 21]                    2   
16    204110029  OTP                          [20, 21]                    2   
17    204110035  OTP              [17, 18, 19, 20, 21]                    5   
18    205110039  OTP              [17, 18, 19, 20, 21]                    5   
19    206110004  OTP                                []                    0   
20    206110011  OTP                                []                    0   
21    206110020  OTP                                []                    0   
22    206110032  OTP                                []                    0   
23    206110034  OTP                                []                    0   
24    207110055  OTP                                []                    0   
25    207110082  OTP                  [18, 19, 20, 21]                    4   
26    207110088  OTP                      [19, 20, 21]                    3   
27    207110089  OTP                                []                    0   
28    207140015  OTP                          [15, 21]                    2   
29    208110006  OTP                  [18, 19, 20, 21]                    4   
30    208110021  OTP                          [19, 21]                    2   
31    208110024  OTP                                []                    0   
32    208110029  OTP                                []                    0   
33    208110033  OTP                              [21]                    1   
34    209110005  OTP                  [18, 19, 20, 21]                    4   
35    209110009  OTP                      [19, 20, 21]                    3   
36    209110011  OTP              [17, 18, 19, 20, 21]                    5   
37    209110019  OTP                                []                    0   
38    209110025  OTP                      [19, 20, 21]                    3   
39    210110016  OTP                              [21]                    1   
40    210110054  OTP                                []                    0   
41    211110015  OTP                                []                    0   
42    211110029  OTP                                []                    0   
43    211110047  OTP              [17, 18, 19, 20, 21]                    5   
44    212110003  OTP                              [21]                    1   
45    212110010  OTP                          [20, 21]                    2   
46    212110030  OTP                                []                    0   
47    212110045  OTP                                []                    0   
48    212110049  OTP                              [21]                    1   
49    213110006  OTP                  [16, 18, 20, 21]     

In [41]:
# Remove rows for complete reporting
missing_reports = missing_reports.query('missing_program_len > 0 | missing_stock_len > 0')

# check
# missing_reports.query('missing_program_len == 0 & missing_stock_len > 0')

In [31]:
", ".join(['1', '2', '3'])

'1, 2, 3'

In [32]:
", ".join(map(lambda x: str(x), [1, 2, 3]))

'1, 2, 3'

In [33]:
", ".join(map(lambda x: str(x), reminders.missing_program[2]))

NameError: name 'reminders' is not defined

/home/robert/PycharmProjects/IMAM/ve/lib/python2.7/site-packages/ipykernel/__main__.py:5: FutureWarning: sort(....) is deprecated, use sort_index(.....)


siteid type                   missing_program  missing_program_len  \
0      201110007  OTP                              [19]                    1   
1      201110007  OTP                              [19]                    1   
2      201110021  OTP      [13, 14, 15, 16, 17, 18, 19]                    7   
3      201110021  OTP      [13, 14, 15, 16, 17, 18, 19]                    7   
4      201110026  OTP      [13, 14, 15, 16, 17, 18, 19]                    7   
5      201110026  OTP      [13, 14, 15, 16, 17, 18, 19]                    7   
6      201110029  OTP      [13, 14, 15, 16, 17, 18, 19]                    7   
7      201110029  OTP      [13, 14, 15, 16, 17, 18, 19]                    7   
8      202110019  OTP                      [14, 18, 19]                    3   
9      202110019  OTP                      [14, 18, 19]                    3   
10     202110021  OTP                          [18, 19]                    2   
11     202110021  OTP                          [18, 19]                    2   
12     202110021  OTP                          [18, 19]                    2   
13     202110021  OTP                          [18, 19]                    2   
14     202110027  OTP      [13, 14, 15, 16, 17, 18, 19]                    7   
15     202110027  OTP      [13, 14, 15, 16, 17, 18, 19]                    7   
16     202110068  OTP                              [19]                    1   
17     202110068  OTP                              [19]                    1   
18     202110068  OTP                              [19]                    1   
19     202610001   SC                              [19]                    1   
20     203110053  OTP                          [18, 19]                    2   
21     203110053  OTP                          [18, 19]                    2   
22     204110006  OTP                              [19]                    1   
23     204110006  OTP                              [19]                    1   
24     204110014  OTP                      [17, 18, 19]                    3   
25     204110014  OTP                      [17, 18, 19]                    3   
26     204110014  OTP                      [17, 18, 19]                    3   
27     204110026  OTP                          [18, 19]                    2   
28     204110026  OTP                          [18, 19]                    2   
29     204110035  OTP                      [17, 18, 19]                    3   
30     204110035  OTP                      [17, 18, 19]                    3   
31     204110035  OTP                      [17, 18, 19]                    3   
32     204110035  OTP                      [17, 18, 19]                    3   
33     205110039  OTP                      [17, 18, 19]                    3   
34     205110039  OTP                      [17, 18, 19]                    3   
35     206110011  OTP                              [19]                    1   
36     206110011  OTP                              [19]                    1   
37     206110032  OTP                      [17, 18, 19]                    3   
38     206110032  OTP                      [17, 18, 19]                    3   
39     206110032  OTP                      [17, 18, 19]                    3   
40     207110055  OTP                              [19]                    1   
41     207110055  OTP                              [19]                    1   
42     207110055  OTP                              [19]                    1   
43     207110082  OTP                          [18, 19]                    2   
44     207110082  OTP                          [18, 19]                    2   
45     207110088  OTP                          [18, 19]                    2   
46     207110088  OTP                          [18, 19]                    2   
47     207140015  OTP                  [15, 17, 18, 19]                    4   
48     208110006  OTP              [15, 16, 17, 18, 19]                    5   
49     208

In [215]:
a = ", ".join(map(lambda x: str(x), reminders.missing_program[2]))

b = ", ".join(map(lambda x: str(x), reminders.missing_stock[2]))
print a
print b

13, 14, 15, 16, 17, 18, 19
13, 14, 15, 16, 17, 18, 19


In [34]:
message = ""
message += ' STOCK reports for weeks %s.' % missing_reports.missing_stock[2]
print message

 STOCK reports for weeks [13, 14, 15, 16, 17, 18, 19].


In [36]:
missing_reports

siteid type                   missing_program  missing_program_len  \
0     201110007  OTP                              [19]                    1   
2     201110021  OTP      [13, 14, 15, 16, 17, 18, 19]                    7   
3     201110026  OTP      [13, 14, 15, 16, 17, 18, 19]                    7   
4     201110029  OTP      [13, 14, 15, 16, 17, 18, 19]                    7   
5     202110019  OTP                      [14, 18, 19]                    3   
6     202110021  OTP                          [18, 19]                    2   
7     202110027  OTP      [13, 14, 15, 16, 17, 18, 19]                    7   
9     202110068  OTP                              [19]                    1   
10    202610001   SC                              [19]                    1   
15    203110053  OTP                          [18, 19]                    2   
16    204110006  OTP                              [19]                    1   
17    204110014  OTP                      [17, 18, 19]                    3   
18    204110026  OTP                          [18, 19]                    2   
20    204110035  OTP                      [17, 18, 19]                    3   
21    205110039  OTP                      [17, 18, 19]                    3   
23    206110011  OTP                              [19]                    1   
25    206110032  OTP                      [17, 18, 19]                    3   
27    207110055  OTP                              [19]                    1   
28    207110082  OTP                          [18, 19]                    2   
29    207110088  OTP                          [18, 19]                    2   
31    207140015  OTP                  [15, 17, 18, 19]                    4   
32    208110006  OTP              [15, 16, 17, 18, 19]                    5   
33    208110021  OTP                              [19]                    1   
34    208110024  OTP                              [19]                    1   
35    208110029  OTP                              [19]                    1   
36    208110033  OTP                              [19]                    1   
37    209110005  OTP              [15, 16, 17, 18, 19]                    5   
38    209110009  OTP                              [19]                    1   
39    209110011  OTP                      [17, 18, 19]                    3   
41    209110025  OTP                              [19]                    1   
42    210110016  OTP                                []                    0   
43    211110015  OTP                              [19]                    1   
45    211110047  OTP                      [17, 18, 19]                    3   
50    212110049  OTP                              [19]                    1   
51    213110006  OTP                          [16, 18]                    2   
52    213110012  OTP                      [17, 18, 19]                    3   
54    213110055  OTP                              [19]                    1   
55    213110059  OTP                              [19]                    1   
56    215110001  OTP                              [19]                    1   
57    215110024  OTP          [14, 15, 16, 17, 18, 19]                    6   
58    215110046  OTP          [14, 15, 16, 17, 18, 19]                    6   
59    216110001  OTP          [14, 15, 16, 17, 18, 19]                    6   
60    216110032  OTP                      [17, 18, 19]                    3   
61    217110006  OTP                              [19]                    1   
62    217110028  OTP                          [18, 19]                    2   
65    217110038  OTP                              [18]                    1   
66    218110025  OTP          [14, 15, 16, 17, 18, 19]                    6   
67    218110030  OTP                              [19]                    1   
68    218110053  OTP          [14, 15, 16, 17, 18, 19]                    6   
69    218110063  OTP                          [18, 19]     

In [37]:
missing_reports.query('missing_stock_len > 0 & missing_program_len == 0')

siteid type missing_program  missing_program_len  \
42    210110016  OTP              []                    0   
95    513110028  OTP              []                    0   
163   813110033  OTP              []                    0   
172   816110003  OTP              []                    0   
198   819110016  OTP              []                    0   
218   821110038  OTP              []                    0   
237   821110058  OTP              []                    0   
246   827110013  OTP              []                    0   
282  1704110016  OTP              []                    0   
307  1716110015  OTP              []                    0   
363  1921110017  OTP              []                    0   
385  1944110016  OTP              []                    0   
531  2106110029  OTP              []                    0   
547  2111110003  OTP              []                    0   
570  2115110011  OTP              []                    0   
599  3304210004   SC              []                    0   
631  3319110014  OTP              []                    0   
690  3505110049  OTP              []                    0   
707  3508110015  OTP              []                    0   
754  3514110015  OTP              []                    0   
793  3605110027  OTP              []                    0   
797  3605110058  OTP              []                    0   
816  3611210034   SC              []                    0   

                        missing_stock  missing_stock_len  \
42                           [18, 19]                  2   
95                               [14]                  1   
163                              [19]                  1   
172                              [14]                  1   
198                              [12]                  1   
218                              [19]                  1   
237                              [12]                  1   
246  [12, 13, 14, 15, 16, 17, 18, 19]                  8   
282                              [19]                  1   
307                              [19]                  1   
363                              [17]                  1   
385                              [19]                  1   
531                              [18]                  1   
547                              [19]                  1   
570                              [14]                  1   
599                              [18]                  1   
631                              [19]                  1   
690                              [15]                  1   
707                              [17]                  1   
754                              [13]                  1   
793                              [12]                  1   
797                              [13]                  1   
816                          [13, 14]                  2   

                                                                                                             message  
42                           Dear @contact from @contact.SiteName. Reminder to send  STOCK reports for weeks 18, 19.  
95                               Dear @contact from @contact.SiteName. Reminder to send  STOCK reports for weeks 14.  
163                              Dear @contact from @contact.SiteName. Reminder to send  STOCK reports for weeks 19.  
172                              Dear @contact from @contact.SiteName. Reminder to send  STOCK reports for weeks 14.  
198                              Dear @contact from @contact.SiteName. Reminder to send  STOCK reports for weeks 12.  
218                              Dear @contact from @contact.SiteName. Reminder to send  STOCK reports for weeks 19.  
237                              Dear @contact from @contact.SiteName. Reminder to send  STOCK reports for weeks 12.  
246  Dear @contact from @contact.SiteName. Reminder to send  STOCK reports for weeks 12, 13, 14, 15, 16, 17, 18, 19.  
282                             

In [42]:
# Merge with all contacts

contacts = pd.read_sql_query("select * from registration;", con=engine)

reminders = pd.merge(missing_reports, contacts, on=['siteid', 'type'])

reminders.sort()

/home/robert/PycharmProjects/IMAM/ve/lib/python2.7/site-packages/ipykernel/__main__.py:7: FutureWarning: sort(....) is deprecated, use sort_index(.....)


siteid type                   missing_program  missing_program_len  \
0      201110007  OTP                      [19, 20, 21]                    3   
1      201110007  OTP                      [19, 20, 21]                    3   
2      202110019  OTP              [14, 18, 19, 20, 21]                    5   
3      202110019  OTP              [14, 18, 19, 20, 21]                    5   
4      202110021  OTP                              [21]                    1   
5      202110021  OTP                              [21]                    1   
6      202110021  OTP                              [21]                    1   
7      202110021  OTP                              [21]                    1   
8      202110035  OTP                              [21]                    1   
9      202110035  OTP                              [21]                    1   
10     202110035  OTP                              [21]                    1   
11     202110035  OTP                              [21]                    1   
12     202110068  OTP                              [21]                    1   
13     202110068  OTP                              [21]                    1   
14     202110068  OTP                              [21]                    1   
15     202610001   SC                      [19, 20, 21]                    3   
16     203110053  OTP                      [19, 20, 21]                    3   
17     203110053  OTP                      [19, 20, 21]                    3   
18     204110014  OTP              [17, 18, 19, 20, 21]                    5   
19     204110014  OTP              [17, 18, 19, 20, 21]                    5   
20     204110014  OTP              [17, 18, 19, 20, 21]                    5   
21     204110026  OTP                          [20, 21]                    2   
22     204110026  OTP                          [20, 21]                    2   
23     204110029  OTP                          [20, 21]                    2   
24     204110029  OTP                          [20, 21]                    2   
25     204110035  OTP              [17, 18, 19, 20, 21]                    5   
26     204110035  OTP              [17, 18, 19, 20, 21]                    5   
27     204110035  OTP              [17, 18, 19, 20, 21]                    5   
28     204110035  OTP              [17, 18, 19, 20, 21]                    5   
29     205110039  OTP              [17, 18, 19, 20, 21]                    5   
30     205110039  OTP              [17, 18, 19, 20, 21]                    5   
31     207110082  OTP                  [18, 19, 20, 21]                    4   
32     207110082  OTP                  [18, 19, 20, 21]                    4   
33     207110088  OTP                      [19, 20, 21]                    3   
34     207110088  OTP                      [19, 20, 21]                    3   
35     207110089  OTP                                []                    0   
36     207140015  OTP                          [15, 21]                    2   
37     208110006  OTP                  [18, 19, 20, 21]                    4   
38     208110006  OTP                  [18, 19, 20, 21]                    4   
39     208110006  OTP                  [18, 19, 20, 21]                    4   
40     208110006  OTP                  [18, 19, 20, 21]                    4   
41     208110021  OTP                          [19, 21]                    2   
42     208110021  OTP                          [19, 21]                    2   
43     208110029  OTP                                []                    0   
44     208110029  OTP                                []                    0   
45     208110029  OTP                                []                    0   
46     208110033  OTP                              [21]                    1   
47     208110033  OTP                              [21]                    1   
48     209110005  OTP                  [18, 19, 20, 21]                    4   
49     209

In [43]:
sites = pd.read_sql_query("select * from site;", con=engine)
sites.head()

index      siteid                 sitename state_num lga_num    ward  \
0      0  3601110001               Bagega PHC        36    3601  Bagega   
1      1  3601110002        Kasumka Comm Disp        36    3601  Bagega   
2      2  3601110003              Kawaye Disp        36    3601  Bagega   
3      3  3601110004            Makakari Disp        36    3601  Bagega   
4      4  3601110005  Tungar Daji Disp (Anka)        36    3601  Bagega   

  x_long y_lat notes  
0   None  None  None  
1   None  None  None  
2   None  None  None  
3   None  None  None  
4   None  None  None

In [44]:
reminders_sites = pd.merge(reminders, sites, on=['siteid'])
reminders_sites.head()

siteid type       missing_program  missing_program_len  \
0  201110007  OTP          [19, 20, 21]                    3   
1  201110007  OTP          [19, 20, 21]                    3   
2  202110019  OTP  [14, 18, 19, 20, 21]                    5   
3  202110019  OTP  [14, 18, 19, 20, 21]                    5   
4  202110021  OTP                  [21]                    1   

          missing_stock  missing_stock_len  \
0          [19, 20, 21]                  3   
1          [19, 20, 21]                  3   
2  [14, 18, 19, 20, 21]                  5   
3  [14, 18, 19, 20, 21]                  5   
4                  [21]                  1   

                           contact_uuid             urn              name  \
0  70eaa1cc-40ee-4323-aed3-647767bffcda  +2348134107585      Gracegidado.   
1  c004920d-9463-4176-a672-ce4332583b9d  +2349021245510  Assurance David.   
2  b679ca25-db75-4137-90e5-8dfbc56bfef2  +2348086762757      Ahmed Aminu.   
3  bd5385d4-5953-4a65-829d-1ffd25ae3bb9  +2347033992688       Noel Norah.   
4  2ab2d7c2-b1a5-4cec-857a-a0d06ddaf776  +2348103586218    Salihu Bakura.   

  groups                 first_seen                  last_seen  \
0        2016-10-25 09:10:31.153335 2017-05-29 00:24:49.711304   
1        2016-10-25 09:05:47.222224 2017-05-29 00:24:44.771874   
2        2016-10-25 09:21:41.934179 2017-05-29 00:25:50.772079   
3        2016-10-25 09:03:02.263195 2017-05-29 00:25:55.364913   
4        2016-10-25 09:04:29.325309 2017-05-29 00:26:14.958556   

                       post                      mail  lga_num_x  state_num_x  \
0  Community Health Officer                      None      201.0          2.0   
1  Community Health Officer                      None      201.0          2.0   
2  Community Health Officer  ahmedaminu2044@yahoo.com      202.0          2.0   
3      Technical Assistance                      None      202.0          2.0   
4  Community Health Officer                      None      202.0          2.0   

   index                 sitename state_num_y lga_num_y    ward x_long y_lat  \
0   9360      DONG  HEALTH CLINIC           2       201    DONG   None  None   
1   9360      DONG  HEALTH CLINIC           2       201    DONG   None  None   
2   9404  FUFORE MATERNITY CENTRE           2       202  FUFORE   None  None   
3   9404  FUFORE MATERNITY CENTRE           2       202  FUFORE   None  None   
4   9406   GURIN MATERNITY CENTRE           2       202   GURIN   None  None   

  notes  
0  None  
1  None  
2  None  
3  None  
4  None

In [47]:
pd.set_option('display.max_colwidth', 400)

reminders_sites['message'] = ""


def create_message(row_in_df):
    row_in_df.message = "Dear %s from %s. Reminder to send " % (row_in_df['name'].rstrip('.'), row_in_df.sitename)
    if row_in_df.missing_program_len > 0:
        row_in_df.message += 'PROGRAM reports for weeks %s' % (", ".join(map(lambda x: str(x), row_in_df.missing_program)))
    if row_in_df.missing_program_len > 0 and row_in_df.missing_stock_len > 0:
        row_in_df.message += ' and STOCK reports for weeks %s.' % ( ", ".join(map(lambda x: str(x), row_in_df.missing_stock)))
    elif row_in_df.missing_program_len == 0 and row_in_df.missing_stock_len > 0:
        row_in_df.message += ' STOCK reports for weeks %s.' % ( ", ".join(map(lambda x: str(x), row_in_df.missing_stock)))
    return row_in_df
    
reminders_sites = reminders_sites.apply(create_message, axis=1)
reminders_sites.sort_values('siteid')

# Add the context of missing stock data for Warehouses.

siteid type                   missing_program  missing_program_len  \
0      201110007  OTP                      [19, 20, 21]                    3   
1      201110007  OTP                      [19, 20, 21]                    3   
2      202110019  OTP              [14, 18, 19, 20, 21]                    5   
3      202110019  OTP              [14, 18, 19, 20, 21]                    5   
4      202110021  OTP                              [21]                    1   
5      202110021  OTP                              [21]                    1   
6      202110021  OTP                              [21]                    1   
7      202110021  OTP                              [21]                    1   
11     202110035  OTP                              [21]                    1   
10     202110035  OTP                              [21]                    1   
8      202110035  OTP                              [21]                    1   
9      202110035  OTP                              [21]                    1   
12     202110068  OTP                              [21]                    1   
13     202110068  OTP                              [21]                    1   
14     202110068  OTP                              [21]                    1   
15     203110053  OTP                      [19, 20, 21]                    3   
16     203110053  OTP                      [19, 20, 21]                    3   
19     204110014  OTP              [17, 18, 19, 20, 21]                    5   
17     204110014  OTP              [17, 18, 19, 20, 21]                    5   
18     204110014  OTP              [17, 18, 19, 20, 21]                    5   
21     204110026  OTP                          [20, 21]                    2   
20     204110026  OTP                          [20, 21]                    2   
22     204110029  OTP                          [20, 21]                    2   
23     204110029  OTP                          [20, 21]                    2   
24     204110035  OTP              [17, 18, 19, 20, 21]                    5   
25     204110035  OTP              [17, 18, 19, 20, 21]                    5   
26     204110035  OTP              [17, 18, 19, 20, 21]                    5   
27     204110035  OTP              [17, 18, 19, 20, 21]                    5   
28     205110039  OTP              [17, 18, 19, 20, 21]                    5   
29     205110039  OTP              [17, 18, 19, 20, 21]                    5   
31     207110082  OTP                  [18, 19, 20, 21]                    4   
30     207110082  OTP                  [18, 19, 20, 21]                    4   
32     207110088  OTP                      [19, 20, 21]                    3   
33     207110088  OTP                      [19, 20, 21]                    3   
34     207110089  OTP                                []                    0   
35     208110006  OTP                  [18, 19, 20, 21]                    4   
36     208110006  OTP                  [18, 19, 20, 21]                    4   
37     208110006  OTP                  [18, 19, 20, 21]                    4   
38     208110006  OTP                  [18, 19, 20, 21]                    4   
40     208110021  OTP                          [19, 21]                    2   
39     208110021  OTP                          [19, 21]                    2   
43     208110029  OTP                                []                    0   
41     208110029  OTP                                []                    0   
42     208110029  OTP                                []                    0   
44     208110033  OTP                              [21]                    1   
45     208110033  OTP                              [21]                    1   
46     209110005  OTP                  [18, 19, 20, 21]                    4   
47     209110005  OTP                  [18, 19, 20, 21]                    4   
48     209110009  OTP                      [19, 20, 21]                    3   
49     209

In [47]:
filename = "Weekly Reminders.xlsx"
writer = pd.ExcelWriter(filename, engine='xlsxwriter')
reminders_sites.to_excel(writer,'Sheet1')
writer.save()
writer.close()

In [156]:
(missing_reports['missing_program'] != missing_reports['missing_program'])

0      False
1      False
2      False
3      False
4      False
5      False
6      False
7      False
8      False
9      False
10     False
11     False
12     False
13     False
14     False
15     False
16     False
17     False
18     False
19     False
20     False
21     False
22     False
23     False
24     False
25     False
26     False
27     False
28     False
29     False
30     False
31     False
32     False
33     False
34     False
35     False
36     False
37     False
38     False
39     False
40     False
41     False
42     False
43     False
44     False
45     False
46     False
47     False
48     False
49     False
50     False
51     False
52     False
53     False
54     False
55     False
56     False
57     False
58     False
59     False
60     False
61     False
62     False
63     False
64     False
65     False
66     False
67     False
68     False
69     False
70     False
71     False
72     False
73     False
74     False
75     False
76     False

In [142]:
list(reversed2([1, 2 , 3]))

[3, 2, 1]

In [ ]:
# class list(object):
#    def __init__(self, something_iterable):
#        self.data = []
#        for i in something_iterable:
#            self.data.append(i)

In [138]:
def reversed2(stuff):
    a = len(stuff) - 1
    while a >= 0:
        yield stuff[a]
        a -= 1

In [140]:
a = reversed2([1, 2 , 3])
print next(a)
print next(a)
print next(a)
print next(a)


3
2
1


StopIteration: 

In [119]:
class Example(object):
    def __init__(self):
        self.foobar = 1
    
    def stuff(self, a):
        print a
        
    def __sub__(self, other):
        print "substracting", other
        
    thing = 1
    
example = Example()

In [120]:
example - 34

substracting 34


In [121]:
example.__sub__(34)

substracting 34


In [122]:
example.stuff

<bound method Example.stuff of <__main__.Example object at 0x7fefb87db890>>

In [117]:
example.__dict__

{'foobar': 1}

In [118]:
Example.__dict__

dict_proxy({'__dict__': <attribute '__dict__' of 'Example' objects>,
            '__doc__': None,
            '__init__': <function __main__.__init__>,
            '__module__': '__main__',
            '__weakref__': <attribute '__weakref__' of 'Example' objects>,
            'stuff': <function __main__.stuff>,
            'thing': 1})

In [46]:

# drop all complete reporting if all program and stock reports are present

# stomiss = stomiss.query('missing_stock_len > 0')
# stomiss = stomiss.drop('missing_stock_len', axis=1)


missing_reports.sort_values(by='siteid')

siteid type                   missing_program  missing_program_len  \
0     201110007  OTP                      [19, 20, 21]                    3   
3     202110019  OTP              [14, 18, 19, 20, 21]                    5   
4     202110021  OTP                              [21]                    1   
5     202110035  OTP                              [21]                    1   
6     202110068  OTP                              [21]                    1   
7     202610001   SC                      [19, 20, 21]                    3   
12    203110053  OTP                      [19, 20, 21]                    3   
14    204110014  OTP              [17, 18, 19, 20, 21]                    5   
15    204110026  OTP                          [20, 21]                    2   
16    204110029  OTP                          [20, 21]                    2   
17    204110035  OTP              [17, 18, 19, 20, 21]                    5   
18    205110039  OTP              [17, 18, 19, 20, 21]                    5   
25    207110082  OTP                  [18, 19, 20, 21]                    4   
26    207110088  OTP                      [19, 20, 21]                    3   
27    207110089  OTP                                []                    0   
28    207140015  OTP                          [15, 21]                    2   
29    208110006  OTP                  [18, 19, 20, 21]                    4   
30    208110021  OTP                          [19, 21]                    2   
32    208110029  OTP                                []                    0   
33    208110033  OTP                              [21]                    1   
34    209110005  OTP                  [18, 19, 20, 21]                    4   
35    209110009  OTP                      [19, 20, 21]                    3   
36    209110011  OTP              [17, 18, 19, 20, 21]                    5   
38    209110025  OTP                      [19, 20, 21]                    3   
39    210110016  OTP                              [21]                    1   
43    211110047  OTP              [17, 18, 19, 20, 21]                    5   
44    212110003  OTP                              [21]                    1   
45    212110010  OTP                          [20, 21]                    2   
48    212110049  OTP                              [21]                    1   
49    213110006  OTP                  [16, 18, 20, 21]                    4   
51    213110043  OTP                                []                    0   
52    213110055  OTP                              [21]                    1   
53    213110059  OTP                              [21]                    1   
54    215110001  OTP                              [21]                    1   
56    215110046  OTP                              [21]                    1   
57    216110001  OTP                          [20, 21]                    2   
58    216110032  OTP              [17, 18, 19, 20, 21]                    5   
64    218110025  OTP                  [18, 19, 20, 21]                    4   
65    218110030  OTP                              [21]                    1   
67    219110020  OTP                              [21]                    1   
69    220110023  OTP                              [21]                    1   
74    221110013  OTP                              [21]                    1   
75    221110027  OTP                              [21]                    1   
76    350110031  OTP                  [18, 19, 20, 21]                    4   
78    504110020  OTP                  [18, 19, 20, 21]                    4   
80    504110033  OTP                                []                    0   
82    504210004   SC                              [21]                    1   
813   507110006  OTP  [14, 15, 16, 17, 18, 19, 20, 21]                    8   
83    512110003  OTP                              [21]                    1   
84    512110020  OTP                          [14, 21]     

In [30]:
# Warehouse data - from LGA and State level stocks. 

In [52]:
# Create missing stock reports
warehouse = pd.read_sql_query("select * from warehouse;", con=engine)

In [53]:
warehouse.head()

index                          contact_uuid             urn  \
0  470486113  c0793c5e-c949-486a-b01d-49996805cc62  +2348030842504   
1  470485448  b1df302b-bf57-4b4c-a940-09ef7c756e32  +2348064677876   
2  470485467  18b82ece-68e8-44b2-8379-46b984a3c122  +2348028572763   
3  470485408  18b82ece-68e8-44b2-8379-46b984a3c122  +2348028572763   
4  470485354  18b82ece-68e8-44b2-8379-46b984a3c122  +2348028572763   

                          name groups  siteid  \
0          Magajiya Abdullahi.           2010   
1    Danlami Hammayidi Ismail.           1609   
2  Abdulkadir Muhammad Yasore.           2003   
3  Abdulkadir Muhammad Yasore.           2003   
4  Abdulkadir Muhammad Yasore.           2003   

                         first_seen                         last_seen  \
0  2017-05-15 22:16:10.176848+02:00  2017-05-15 22:20:03.726498+02:00   
1  2017-05-15 21:39:47.181978+02:00  2017-05-15 22:00:49.318194+02:00   
2  2017-05-15 21:44:06.171531+02:00  2017-05-15 21:53:31.938373+02:00   
3  2017-05-15 21:30:39.392809+02:00  2017-05-15 21:38:43.719674+02:00   
4  2017-05-15 21:19:47.582253+02:00  2017-05-15 21:25:57.148830+02:00   

   weeknum  year  rutf_in  rutf_out  rutf_bal  
0       17  2017      0.0       0.0       0.0  
1       18  2017    350.0     335.0      18.0  
2       20  2017      0.0     150.0      20.0  
3       19  2017    259.0     159.0     170.0  
4       18  2017      0.0       0.0      70.0

In [50]:
# Introducing Year for analysis

# must loop over the data in the pandas series to assign the new variable with isocalendar
# warehouse['year'] = warehouse.last_seen.isocalendar()[0]

# warehouse['year'] = warehouse['last_seen'].map(lambda x: x.isocalendar()[0])
# print(warehouse['year'].value_counts())

# we don't need to do that anymore since we do that during importation

2017    2385
2016    1758
Name: year, dtype: int64


In [54]:
# Weeknum data are not clean - not int
warehouse.weeknum = pd.to_numeric(warehouse.weeknum, errors='coerce')

# Clean out of range identification data - this deletes entire row where a NaN is found
# week 52 should not be hard coded. 
warehouse = warehouse.query('weeknum==weeknum').query('weeknum>=1').query('weeknum<=52')
# Convert from float to int
warehouse.weeknum = warehouse.weeknum.astype(int)

print len(warehouse.weeknum)
#print warehouse.weeknum.value_counts(sort = True)

4138


In [55]:
warehouse['year_weeknum'] = zip(warehouse['year'], warehouse['weeknum'])
warehouse['iso_year_weeknum'] = warehouse['year_weeknum'].map(lambda x: Week(x[0], x[1]))

year, week, _ = date.today().isocalendar()
current_week = Week(year, week)

# since how many week this report is about
warehouse['since_x_weeks'] = warehouse['iso_year_weeknum'].map(lambda x: current_week - x)

In [56]:
# There are no types per se in warehouse data.  All sites are warehouses. 
# to make the code more generic, assign correction to type variable in import_warehouse
# then all warehouses sites will be coded as 'sup'.

# For variable below - will not show output if referred to as warehouse.type only as warehouse['type']
warehouse['type'] = "Sup"
warehouse['type'].value_counts()

Sup    4138
Name: type, dtype: int64

In [57]:
# Merge siteID with first and second that all inactive sites are included in the analysis

# Need to add first and second
first = pd.read_sql_query("select * from First_admin;", con=engine)
first['siteid'] = first.state_num
first['sitename'] = first.state



second = pd.read_sql_query("select * from second_admin;", con=engine)
second['siteid'] = second.lga_num
second['sitename'] = second.lga

supervision_sites = pd.concat([second, first])
supervision_sites

index             lga  lga_num  siteid        sitename    state state_num
0     9354           DEMSA    201.0     201           DEMSA      NaN         2
1     9386          FUFORE    202.0     202          FUFORE      NaN         2
2     9462           GANYE    203.0     203           GANYE      NaN         2
3     9524           GIREI    204.0     204           GIREI      NaN         2
4     9561           GOMBI    205.0     205           GOMBI      NaN         2
5     9612           GUYUK    206.0     206           GUYUK      NaN         2
6     9662            HONG    207.0     207            HONG      NaN         2
7     9751            JADA    208.0     208            JADA      NaN         2
8     9784         LAMURDE    209.0     209         LAMURDE      NaN         2
9     9812        MADAGALI    210.0     210        MADAGALI      NaN         2
10    9870           MAIHA    211.0     211           MAIHA      NaN         2
11    9931     MAYO-BALEWA    212.0     212     MAYO-BALEWA      NaN         2
12    9980         MICHIKA    213.0     213         MICHIKA      NaN         2
13   10042      MUBI NORTH    214.0     214      MUBI NORTH      NaN         2
14   10089      MUBI-SOUTH    215.0     215      MUBI-SOUTH      NaN         2
15   10135           NUMAN    216.0     216           NUMAN      NaN         2
16   10172        SHELLENG    217.0     217        SHELLENG      NaN         2
17   10215            SONG    218.0     218            SONG      NaN         2
18   10286          TOUNGO    219.0     219          TOUNGO      NaN         2
19   10308      YOLA NORTH    220.0     220      YOLA NORTH      NaN         2
20   10353      YOLA SOUTH    221.0     221      YOLA SOUTH      NaN         2
21    8319        ALKALERI    501.0     501        ALKALERI      NaN         5
22    8361          BAUCHI    502.0     502          BAUCHI      NaN         5
23    8463          BOGORO    503.0     503          BOGORO      NaN         5
24    8489          DAMBAM    504.0     504          DAMBAM      NaN         5
25    8526          DARAZO    505.0     505          DARAZO      NaN         5
26    8579            DASS    506.0     506            DASS      NaN         5
27    8613          GAMAWA    507.0     507          GAMAWA      NaN         5
28    8667         GANJUWA    508.0     508         GANJUWA      NaN         5
29    8737           GIADE    509.0     509           GIADE      NaN         5
30    8775      ITAS-GADAU    510.0     510      ITAS-GADAU      NaN         5
31    8810        JAMA'ARE    511.0     511        JAMA'ARE      NaN         5
32    8837         KATAGUM    512.0     512         KATAGUM      NaN         5
33    8881           KIRFI    513.0     513           KIRFI      NaN         5
34    8923           MISAU    514.0     514           MISAU      NaN         5
35    8975           NINGI    515.0     515           NINGI      NaN         5
36    9033           SHIRA    516.0     516           SHIRA      NaN         5
37    9078   TAFAWA-BALEWA    517.0     517   TAFAWA-BALEWA      NaN         5
38    9130            TORO    518.0     518            TORO      NaN         5
39    9254           WARJI    519.0     519           WARJI      NaN         5
40    9295            ZAKI    520.0     520            ZAKI      NaN         5
41    7742          ABADAM    801.0     801          ABADAM      NaN         8
42    7753      ASKIRA UBA    802.0     802      ASKIRA UBA      NaN         8
43    7777            BAMA    803.0     803            BAMA      NaN         8
44    7810            BAYO    804.0     804            BAYO      NaN         8
45    7835             BIU    805.0     805             BIU      NaN         8
46    7857          CHIBOK    806.0     806          CHIBOK      NaN         8
47    7875          DAMBOA    807.0     807          DAMBOA      NaN         8
48    7896           DIKWA    808.0     808           DIKWA      NaN         8
49    7908           GUBIO    809.0     809           G

In [58]:
# stock missing reports

# remove all cases that are not supervision level - with site id more than 101110001

stomiss = warehouse.query('since_x_weeks>0')\
        .query('since_x_weeks<=8')\
        .query('siteid<101110001')\
        .groupby(['siteid', 'type'])['weeknum']\
        .unique()\
        .map(lambda x: list(sorted(set(range(week - 8, week)) - set(x))))\
        .to_frame()
        


In [59]:
stomiss = stomiss.reset_index()
stomiss = stomiss.rename(index = str, columns = {"weeknum": "missing_stock"})

In [61]:
stomiss.sort_values('siteid')

siteid type                 missing_stock
0         2  Sup                          [21]
1         8  Sup              [18, 19, 20, 21]
2        16  Sup                  [19, 20, 21]
3        17  Sup      [16, 17, 18, 19, 20, 21]
4        18  Sup                          [21]
5        19  Sup                          [21]
6        20  Sup                          [21]
7        21  Sup                          [21]
8        33  Sup                            []
9        35  Sup                            []
10       36  Sup                            []
11      201  Sup                          [21]
12      202  Sup                  [16, 17, 21]
13      203  Sup                  [19, 20, 21]
14      204  Sup                          [21]
15      205  Sup                          [21]
16      207  Sup                            []
17      208  Sup      [15, 17, 18, 19, 20, 21]
18      211  Sup                            []
19      212  Sup                          [21]
20      213  Sup                          [21]
21      214  Sup                          [21]
22      216  Sup                          [21]
23      217  Sup                          [21]
24      219  Sup                          [21]
25      220  Sup                      [20, 21]
26      221  Sup                          [21]
27      513  Sup  [15, 16, 17, 18, 19, 20, 21]
28      802  Sup                          [21]
29      805  Sup                          [21]
30      807  Sup      [15, 17, 18, 19, 20, 21]
31      809  Sup  [15, 16, 17, 18, 19, 20, 21]
32      819  Sup              [17, 18, 19, 21]
33      825  Sup                      [14, 21]
34      827  Sup          [15, 16, 17, 20, 21]
35     1604  Sup                  [17, 20, 21]
36     1606  Sup                          [21]
37     1609  Sup                          [21]
38     1702  Sup                  [19, 20, 21]
39     1704  Sup                      [15, 21]
40     1710  Sup                          [21]
41     1712  Sup      [16, 17, 18, 19, 20, 21]
42     1714  Sup                          [21]
43     1716  Sup          [17, 18, 19, 20, 21]
44     1717  Sup                          [21]
45     1719  Sup                          [21]
46     1720  Sup          [17, 18, 19, 20, 21]
47     1724  Sup                            []
48     1727  Sup              [17, 19, 20, 21]
49     1818  Sup                          [21]
50     1823  Sup                          [21]
51     1905  Sup                            []
52     1921  Sup                            []
53     1928  Sup                            []
54     1936  Sup                            []
55     1940  Sup                          [21]
56     1944  Sup                      [20, 21]
57     2001  Sup                            []
58     2003  Sup                            []
59     2004  Sup                            []
60     2005  Sup  [15, 16, 17, 18, 19, 20, 21]
61     2007  Sup                            []
62     2010  Sup                          [21]
63     2011  Sup                          [21]
64     2015  Sup                          [15]
65     2016  Sup                          [21]
66     2018  Sup                          [21]
67     2024  Sup                          [21]
68     2026  Sup                            []
69     2027  Sup                  [16, 20, 21]
70     2033  Sup                          [21]
71     2034  Sup                  [19, 20, 21]
72     2102  Sup          [17, 18, 19, 20, 21]
73     2103  Sup                      [20, 21]
74     2104  Sup      [16, 17, 18, 19, 20, 21]
75     2105  Sup          [17, 18, 19, 20, 21]
76     2106  Sup                          [21]
77     2108  Sup                            []
78     2109  Sup              [18, 19, 20, 21]
79     2111  Sup                      [20, 21]
80     2112  Sup                            []
81     2113  Sup                            []
82     2114  Sup                          [21]
83     2117  Sup                          [21]
84     211

In [63]:
supervision_stomiss = pd.merge(supervision_sites, stomiss, on='siteid', how='outer')
supervision_stomiss

index             lga  lga_num  siteid        sitename    state  \
0     9354           DEMSA    201.0     201           DEMSA      NaN   
1     9386          FUFORE    202.0     202          FUFORE      NaN   
2     9462           GANYE    203.0     203           GANYE      NaN   
3     9524           GIREI    204.0     204           GIREI      NaN   
4     9561           GOMBI    205.0     205           GOMBI      NaN   
5     9612           GUYUK    206.0     206           GUYUK      NaN   
6     9662            HONG    207.0     207            HONG      NaN   
7     9751            JADA    208.0     208            JADA      NaN   
8     9784         LAMURDE    209.0     209         LAMURDE      NaN   
9     9812        MADAGALI    210.0     210        MADAGALI      NaN   
10    9870           MAIHA    211.0     211           MAIHA      NaN   
11    9931     MAYO-BALEWA    212.0     212     MAYO-BALEWA      NaN   
12    9980         MICHIKA    213.0     213         MICHIKA      NaN   
13   10042      MUBI NORTH    214.0     214      MUBI NORTH      NaN   
14   10089      MUBI-SOUTH    215.0     215      MUBI-SOUTH      NaN   
15   10135           NUMAN    216.0     216           NUMAN      NaN   
16   10172        SHELLENG    217.0     217        SHELLENG      NaN   
17   10215            SONG    218.0     218            SONG      NaN   
18   10286          TOUNGO    219.0     219          TOUNGO      NaN   
19   10308      YOLA NORTH    220.0     220      YOLA NORTH      NaN   
20   10353      YOLA SOUTH    221.0     221      YOLA SOUTH      NaN   
21    8319        ALKALERI    501.0     501        ALKALERI      NaN   
22    8361          BAUCHI    502.0     502          BAUCHI      NaN   
23    8463          BOGORO    503.0     503          BOGORO      NaN   
24    8489          DAMBAM    504.0     504          DAMBAM      NaN   
25    8526          DARAZO    505.0     505          DARAZO      NaN   
26    8579            DASS    506.0     506            DASS      NaN   
27    8613          GAMAWA    507.0     507          GAMAWA      NaN   
28    8667         GANJUWA    508.0     508         GANJUWA      NaN   
29    8737           GIADE    509.0     509           GIADE      NaN   
30    8775      ITAS-GADAU    510.0     510      ITAS-GADAU      NaN   
31    8810        JAMA'ARE    511.0     511        JAMA'ARE      NaN   
32    8837         KATAGUM    512.0     512         KATAGUM      NaN   
33    8881           KIRFI    513.0     513           KIRFI      NaN   
34    8923           MISAU    514.0     514           MISAU      NaN   
35    8975           NINGI    515.0     515           NINGI      NaN   
36    9033           SHIRA    516.0     516           SHIRA      NaN   
37    9078   TAFAWA-BALEWA    517.0     517   TAFAWA-BALEWA      NaN   
38    9130            TORO    518.0     518            TORO      NaN   
39    9254           WARJI    519.0     519           WARJI      NaN   
40    9295            ZAKI    520.0     520            ZAKI      NaN   
41    7742          ABADAM    801.0     801          ABADAM      NaN   
42    7753      ASKIRA UBA    802.0     802      ASKIRA UBA      NaN   
43    7777            BAMA    803.0     803            BAMA      NaN   
44    7810            BAYO    804.0     804            BAYO      NaN   
45    7835             BIU    805.0     805             BIU      NaN   
46    7857          CHIBOK    806.0     806          CHIBOK      NaN   
47    7875          DAMBOA    807.0     807          DAMBOA      NaN   
48    7896           DIKWA    808.0     808           DIKWA      NaN   
49    7908           GUBIO    809.0     809           GUBIO      NaN   
50    7916        GUZAMALA    810.0     810        GUZAMALA      NaN   
51    7929           GWOZA    811.0     811           GWOZA      NaN   
52    7963           HAWUL    812.0     812           HAWUL      NaN   
53    7985            JERE    813.0     813            JERE      NaN   
54    8030            KAGA    814.0     814  

In [64]:
supervision_stomiss['missing_stock'] = supervision_stomiss['missing_stock'].map(lambda x: x if x == x else target_weeks)

supervision_stomiss['missing_stock_len'] = supervision_stomiss.missing_stock.map(lambda x:(len(x)))
supervision_stomiss

index             lga  lga_num  siteid        sitename    state  \
0     9354           DEMSA    201.0     201           DEMSA      NaN   
1     9386          FUFORE    202.0     202          FUFORE      NaN   
2     9462           GANYE    203.0     203           GANYE      NaN   
3     9524           GIREI    204.0     204           GIREI      NaN   
4     9561           GOMBI    205.0     205           GOMBI      NaN   
5     9612           GUYUK    206.0     206           GUYUK      NaN   
6     9662            HONG    207.0     207            HONG      NaN   
7     9751            JADA    208.0     208            JADA      NaN   
8     9784         LAMURDE    209.0     209         LAMURDE      NaN   
9     9812        MADAGALI    210.0     210        MADAGALI      NaN   
10    9870           MAIHA    211.0     211           MAIHA      NaN   
11    9931     MAYO-BALEWA    212.0     212     MAYO-BALEWA      NaN   
12    9980         MICHIKA    213.0     213         MICHIKA      NaN   
13   10042      MUBI NORTH    214.0     214      MUBI NORTH      NaN   
14   10089      MUBI-SOUTH    215.0     215      MUBI-SOUTH      NaN   
15   10135           NUMAN    216.0     216           NUMAN      NaN   
16   10172        SHELLENG    217.0     217        SHELLENG      NaN   
17   10215            SONG    218.0     218            SONG      NaN   
18   10286          TOUNGO    219.0     219          TOUNGO      NaN   
19   10308      YOLA NORTH    220.0     220      YOLA NORTH      NaN   
20   10353      YOLA SOUTH    221.0     221      YOLA SOUTH      NaN   
21    8319        ALKALERI    501.0     501        ALKALERI      NaN   
22    8361          BAUCHI    502.0     502          BAUCHI      NaN   
23    8463          BOGORO    503.0     503          BOGORO      NaN   
24    8489          DAMBAM    504.0     504          DAMBAM      NaN   
25    8526          DARAZO    505.0     505          DARAZO      NaN   
26    8579            DASS    506.0     506            DASS      NaN   
27    8613          GAMAWA    507.0     507          GAMAWA      NaN   
28    8667         GANJUWA    508.0     508         GANJUWA      NaN   
29    8737           GIADE    509.0     509           GIADE      NaN   
30    8775      ITAS-GADAU    510.0     510      ITAS-GADAU      NaN   
31    8810        JAMA'ARE    511.0     511        JAMA'ARE      NaN   
32    8837         KATAGUM    512.0     512         KATAGUM      NaN   
33    8881           KIRFI    513.0     513           KIRFI      NaN   
34    8923           MISAU    514.0     514           MISAU      NaN   
35    8975           NINGI    515.0     515           NINGI      NaN   
36    9033           SHIRA    516.0     516           SHIRA      NaN   
37    9078   TAFAWA-BALEWA    517.0     517   TAFAWA-BALEWA      NaN   
38    9130            TORO    518.0     518            TORO      NaN   
39    9254           WARJI    519.0     519           WARJI      NaN   
40    9295            ZAKI    520.0     520            ZAKI      NaN   
41    7742          ABADAM    801.0     801          ABADAM      NaN   
42    7753      ASKIRA UBA    802.0     802      ASKIRA UBA      NaN   
43    7777            BAMA    803.0     803            BAMA      NaN   
44    7810            BAYO    804.0     804            BAYO      NaN   
45    7835             BIU    805.0     805             BIU      NaN   
46    7857          CHIBOK    806.0     806          CHIBOK      NaN   
47    7875          DAMBOA    807.0     807          DAMBOA      NaN   
48    7896           DIKWA    808.0     808           DIKWA      NaN   
49    7908           GUBIO    809.0     809           GUBIO      NaN   
50    7916        GUZAMALA    810.0     810        GUZAMALA      NaN   
51    7929           GWOZA    811.0     811           GWOZA      NaN   
52    7963           HAWUL    812.0     812           HAWUL      NaN   
53    7985            JERE    813.0     813            JERE      NaN   
54    8030            KAGA    814.0     814  

In [65]:
supervision_stomiss = supervision_stomiss.query('missing_stock_len > 0')
supervision_stomiss

index             lga  lga_num  siteid        sitename    state  \
0     9354           DEMSA    201.0     201           DEMSA      NaN   
1     9386          FUFORE    202.0     202          FUFORE      NaN   
2     9462           GANYE    203.0     203           GANYE      NaN   
3     9524           GIREI    204.0     204           GIREI      NaN   
4     9561           GOMBI    205.0     205           GOMBI      NaN   
5     9612           GUYUK    206.0     206           GUYUK      NaN   
7     9751            JADA    208.0     208            JADA      NaN   
8     9784         LAMURDE    209.0     209         LAMURDE      NaN   
9     9812        MADAGALI    210.0     210        MADAGALI      NaN   
11    9931     MAYO-BALEWA    212.0     212     MAYO-BALEWA      NaN   
12    9980         MICHIKA    213.0     213         MICHIKA      NaN   
13   10042      MUBI NORTH    214.0     214      MUBI NORTH      NaN   
14   10089      MUBI-SOUTH    215.0     215      MUBI-SOUTH      NaN   
15   10135           NUMAN    216.0     216           NUMAN      NaN   
16   10172        SHELLENG    217.0     217        SHELLENG      NaN   
17   10215            SONG    218.0     218            SONG      NaN   
18   10286          TOUNGO    219.0     219          TOUNGO      NaN   
19   10308      YOLA NORTH    220.0     220      YOLA NORTH      NaN   
20   10353      YOLA SOUTH    221.0     221      YOLA SOUTH      NaN   
21    8319        ALKALERI    501.0     501        ALKALERI      NaN   
22    8361          BAUCHI    502.0     502          BAUCHI      NaN   
23    8463          BOGORO    503.0     503          BOGORO      NaN   
24    8489          DAMBAM    504.0     504          DAMBAM      NaN   
25    8526          DARAZO    505.0     505          DARAZO      NaN   
26    8579            DASS    506.0     506            DASS      NaN   
27    8613          GAMAWA    507.0     507          GAMAWA      NaN   
28    8667         GANJUWA    508.0     508         GANJUWA      NaN   
29    8737           GIADE    509.0     509           GIADE      NaN   
30    8775      ITAS-GADAU    510.0     510      ITAS-GADAU      NaN   
31    8810        JAMA'ARE    511.0     511        JAMA'ARE      NaN   
32    8837         KATAGUM    512.0     512         KATAGUM      NaN   
33    8881           KIRFI    513.0     513           KIRFI      NaN   
34    8923           MISAU    514.0     514           MISAU      NaN   
35    8975           NINGI    515.0     515           NINGI      NaN   
36    9033           SHIRA    516.0     516           SHIRA      NaN   
37    9078   TAFAWA-BALEWA    517.0     517   TAFAWA-BALEWA      NaN   
38    9130            TORO    518.0     518            TORO      NaN   
39    9254           WARJI    519.0     519           WARJI      NaN   
40    9295            ZAKI    520.0     520            ZAKI      NaN   
41    7742          ABADAM    801.0     801          ABADAM      NaN   
42    7753      ASKIRA UBA    802.0     802      ASKIRA UBA      NaN   
43    7777            BAMA    803.0     803            BAMA      NaN   
44    7810            BAYO    804.0     804            BAYO      NaN   
45    7835             BIU    805.0     805             BIU      NaN   
46    7857          CHIBOK    806.0     806          CHIBOK      NaN   
47    7875          DAMBOA    807.0     807          DAMBOA      NaN   
48    7896           DIKWA    808.0     808           DIKWA      NaN   
49    7908           GUBIO    809.0     809           GUBIO      NaN   
50    7916        GUZAMALA    810.0     810        GUZAMALA      NaN   
51    7929           GWOZA    811.0     811           GWOZA      NaN   
52    7963           HAWUL    812.0     812           HAWUL      NaN   
53    7985            JERE    813.0     813            JERE      NaN   
54    8030            KAGA    814.0     814            KAGA      NaN   
55    8045      KALA BALGE    815.0     815      KALA BALGE      NaN   
56    8057         KONDUGA    816.0     816  

In [66]:
# merge with contacts
contacts = pd.read_sql_query("select * from registration;", con=engine)

# If using same code as implementation - then add type
warehouse_reminders = pd.merge(supervision_stomiss, contacts, on=['siteid'])

warehouse_reminders.sort()

/home/robert/PycharmProjects/IMAM/ve/lib/python2.7/site-packages/ipykernel/__main__.py:7: FutureWarning: sort(....) is deprecated, use sort_index(.....)


index             lga  lga_num_x  siteid        sitename    state  \
0     9354           DEMSA      201.0     201           DEMSA      NaN   
1     9386          FUFORE      202.0     202          FUFORE      NaN   
2     9386          FUFORE      202.0     202          FUFORE      NaN   
3     9386          FUFORE      202.0     202          FUFORE      NaN   
4     9462           GANYE      203.0     203           GANYE      NaN   
5     9524           GIREI      204.0     204           GIREI      NaN   
6     9524           GIREI      204.0     204           GIREI      NaN   
7     9561           GOMBI      205.0     205           GOMBI      NaN   
8     9561           GOMBI      205.0     205           GOMBI      NaN   
9     9612           GUYUK      206.0     206           GUYUK      NaN   
10    9751            JADA      208.0     208            JADA      NaN   
11    9751            JADA      208.0     208            JADA      NaN   
12    9784         LAMURDE      209.0     209         LAMURDE      NaN   
13    9812        MADAGALI      210.0     210        MADAGALI      NaN   
14    9812        MADAGALI      210.0     210        MADAGALI      NaN   
15    9931     MAYO-BALEWA      212.0     212     MAYO-BALEWA      NaN   
16    9931     MAYO-BALEWA      212.0     212     MAYO-BALEWA      NaN   
17    9980         MICHIKA      213.0     213         MICHIKA      NaN   
18   10042      MUBI NORTH      214.0     214      MUBI NORTH      NaN   
19   10042      MUBI NORTH      214.0     214      MUBI NORTH      NaN   
20   10089      MUBI-SOUTH      215.0     215      MUBI-SOUTH      NaN   
21   10135           NUMAN      216.0     216           NUMAN      NaN   
22   10172        SHELLENG      217.0     217        SHELLENG      NaN   
23   10215            SONG      218.0     218            SONG      NaN   
24   10215            SONG      218.0     218            SONG      NaN   
25   10286          TOUNGO      219.0     219          TOUNGO      NaN   
26   10308      YOLA NORTH      220.0     220      YOLA NORTH      NaN   
27   10353      YOLA SOUTH      221.0     221      YOLA SOUTH      NaN   
28    8489          DAMBAM      504.0     504          DAMBAM      NaN   
29    8837         KATAGUM      512.0     512         KATAGUM      NaN   
30    8881           KIRFI      513.0     513           KIRFI      NaN   
31    7753      ASKIRA UBA      802.0     802      ASKIRA UBA      NaN   
32    7753      ASKIRA UBA      802.0     802      ASKIRA UBA      NaN   
33    7753      ASKIRA UBA      802.0     802      ASKIRA UBA      NaN   
34    7777            BAMA      803.0     803            BAMA      NaN   
35    7810            BAYO      804.0     804            BAYO      NaN   
36    7835             BIU      805.0     805             BIU      NaN   
37    7835             BIU      805.0     805             BIU      NaN   
38    7857          CHIBOK      806.0     806          CHIBOK      NaN   
39    7857          CHIBOK      806.0     806          CHIBOK      NaN   
40    7875          DAMBOA      807.0     807          DAMBOA      NaN   
41    7875          DAMBOA      807.0     807          DAMBOA      NaN   
42    7896           DIKWA      808.0     808           DIKWA      NaN   
43    7908           GUBIO      809.0     809           GUBIO      NaN   
44    7929           GWOZA      811.0     811           GWOZA      NaN   
45    7963           HAWUL      812.0     812           HAWUL      NaN   
46    7963           HAWUL      812.0     812           HAWUL      NaN   
47    7963           HAWUL      812.0     812           HAWUL      NaN   
48    7985            JERE      813.0     813            JERE      NaN   
49    7985            JERE      813.0     813            JERE      NaN   
50    7985            JERE      813.0     813            JERE      NaN   
51    7985            JERE      813.0     813            JERE      NaN   
52    8030            KAGA      814.0     814            KAGA      NaN   
53    804

In [67]:
pd.set_option('display.max_colwidth', 400)

warehouse_reminders['message'] = ""

def create_message(row_in_df):
    row_in_df.message = "Dear %s from %s. Reminder to send " % (row_in_df['name'].rstrip('.'), row_in_df.sitename)
    row_in_df.message += ' STOCK reports for weeks %s.' % ( ", ".join(map(lambda x: str(x), row_in_df.missing_stock)))
    return row_in_df
    
warehouse_reminders = warehouse_reminders.apply(create_message, axis=1)
warehouse_reminders

index             lga  lga_num_x  siteid        sitename    state  \
0     9354           DEMSA      201.0     201           DEMSA      NaN   
1     9386          FUFORE      202.0     202          FUFORE      NaN   
2     9386          FUFORE      202.0     202          FUFORE      NaN   
3     9386          FUFORE      202.0     202          FUFORE      NaN   
4     9462           GANYE      203.0     203           GANYE      NaN   
5     9524           GIREI      204.0     204           GIREI      NaN   
6     9524           GIREI      204.0     204           GIREI      NaN   
7     9561           GOMBI      205.0     205           GOMBI      NaN   
8     9561           GOMBI      205.0     205           GOMBI      NaN   
9     9612           GUYUK      206.0     206           GUYUK      NaN   
10    9751            JADA      208.0     208            JADA      NaN   
11    9751            JADA      208.0     208            JADA      NaN   
12    9784         LAMURDE      209.0     209         LAMURDE      NaN   
13    9812        MADAGALI      210.0     210        MADAGALI      NaN   
14    9812        MADAGALI      210.0     210        MADAGALI      NaN   
15    9931     MAYO-BALEWA      212.0     212     MAYO-BALEWA      NaN   
16    9931     MAYO-BALEWA      212.0     212     MAYO-BALEWA      NaN   
17    9980         MICHIKA      213.0     213         MICHIKA      NaN   
18   10042      MUBI NORTH      214.0     214      MUBI NORTH      NaN   
19   10042      MUBI NORTH      214.0     214      MUBI NORTH      NaN   
20   10089      MUBI-SOUTH      215.0     215      MUBI-SOUTH      NaN   
21   10135           NUMAN      216.0     216           NUMAN      NaN   
22   10172        SHELLENG      217.0     217        SHELLENG      NaN   
23   10215            SONG      218.0     218            SONG      NaN   
24   10215            SONG      218.0     218            SONG      NaN   
25   10286          TOUNGO      219.0     219          TOUNGO      NaN   
26   10308      YOLA NORTH      220.0     220      YOLA NORTH      NaN   
27   10353      YOLA SOUTH      221.0     221      YOLA SOUTH      NaN   
28    8489          DAMBAM      504.0     504          DAMBAM      NaN   
29    8837         KATAGUM      512.0     512         KATAGUM      NaN   
30    8881           KIRFI      513.0     513           KIRFI      NaN   
31    7753      ASKIRA UBA      802.0     802      ASKIRA UBA      NaN   
32    7753      ASKIRA UBA      802.0     802      ASKIRA UBA      NaN   
33    7753      ASKIRA UBA      802.0     802      ASKIRA UBA      NaN   
34    7777            BAMA      803.0     803            BAMA      NaN   
35    7810            BAYO      804.0     804            BAYO      NaN   
36    7835             BIU      805.0     805             BIU      NaN   
37    7835             BIU      805.0     805             BIU      NaN   
38    7857          CHIBOK      806.0     806          CHIBOK      NaN   
39    7857          CHIBOK      806.0     806          CHIBOK      NaN   
40    7875          DAMBOA      807.0     807          DAMBOA      NaN   
41    7875          DAMBOA      807.0     807          DAMBOA      NaN   
42    7896           DIKWA      808.0     808           DIKWA      NaN   
43    7908           GUBIO      809.0     809           GUBIO      NaN   
44    7929           GWOZA      811.0     811           GWOZA      NaN   
45    7963           HAWUL      812.0     812           HAWUL      NaN   
46    7963           HAWUL      812.0     812           HAWUL      NaN   
47    7963           HAWUL      812.0     812           HAWUL      NaN   
48    7985            JERE      813.0     813            JERE      NaN   
49    7985            JERE      813.0     813            JERE      NaN   
50    7985            JERE      813.0     813            JERE      NaN   
51    7985            JERE      813.0     813            JERE      NaN   
52    8030            KAGA      814.0     814            KAGA      NaN   
53    804

In [38]:
stomiss

# sites with no reports in past 8 weeks do not have any reports in this current report

# 206 Guyuk LGA missing information
# Hannatu B Usman reported for Guyuk LGA on April 5 2017

# 210 Madagali LGA missing information
# Adama Abubakar

# 215 Mubi South LGA missing information
# Grace John

# 504 Mubi South LGA missing information
# Ahmed Idi Dagauda

# 804 Bayo LGA missing information
# Hauwa Aliyu

# 806 Chibok LGA missing information
# Pana Tapchi

# If SiteID is present and the list is [] then all reports are complete. 
# If SiteID is missing in list of missing reports, then all reports are missing.
# merge reports from contacts list
# verify reports and set reports to missing. 


siteid type                     missing_stock
0         2  Sup                              [19]
1         8  Sup                          [18, 19]
2        16  Sup                              [19]
3        17  Sup                  [16, 17, 18, 19]
4        18  Sup                              [19]
5        19  Sup                                []
6        20  Sup                          [18, 19]
7        21  Sup                                []
8        33  Sup                                []
9        35  Sup                              [19]
10       36  Sup                              [19]
11      201  Sup                                []
12      202  Sup                          [16, 17]
13      203  Sup                          [18, 19]
14      204  Sup                              [19]
15      205  Sup                              [19]
16      207  Sup                              [19]
17      208  Sup          [14, 15, 16, 17, 18, 19]
18      209  Sup      [13, 14, 15, 16, 17, 18, 19]
19      211  Sup                                []
20      212  Sup                              [19]
21      213  Sup                          [18, 19]
22      214  Sup                      [17, 18, 19]
23      216  Sup                              [19]
24      217  Sup                              [19]
25      218  Sup  [12, 13, 14, 15, 16, 17, 18, 19]
26      219  Sup                  [16, 17, 18, 19]
27      220  Sup                              [19]
28      221  Sup                              [19]
29      513  Sup              [15, 16, 17, 18, 19]
30      802  Sup                              [19]
31      805  Sup                              [19]
32      807  Sup                      [17, 18, 19]
33      809  Sup              [15, 16, 17, 18, 19]
34      819  Sup                      [17, 18, 19]
35      825  Sup                      [15, 18, 19]
36      827  Sup          [14, 15, 16, 17, 18, 19]
37     1604  Sup                                []
38     1606  Sup                                []
39     1609  Sup                              [19]
40     1702  Sup                              [19]
41     1704  Sup                          [15, 19]
42     1710  Sup                      [17, 18, 19]
43     1712  Sup                      [17, 18, 19]
44     1714  Sup                              [19]
45     1716  Sup                      [17, 18, 19]
46     1717  Sup                              [19]
47     1719  Sup                          [18, 19]
48     1720  Sup                      [17, 18, 19]
49     1724  Sup                              [19]
50     1727  Sup                          [18, 19]
51     1818  Sup                                []
52     1823  Sup                                []
53     1905  Sup                                []
54     1921  Sup                                []
55     1928  Sup                              [19]
56     1936  Sup                                []
57     1940  Sup                              [19]
58     1944  Sup                                []
59     2001  Sup                                []
60     2003  Sup                  [15, 17, 18, 19]
61     2004  Sup                              [19]
62     2005  Sup              [15, 16, 17, 18, 19]
63     2007  Sup                              [19]
64     2010  Sup                              [19]
65     2011  Sup                          [18, 19]
66     2015  Sup              [15, 16, 17, 18, 19]
67     2016  Sup                              [19]
68     2018  Sup                                []
69     2024  Sup                              [19]
70     2026  Sup                              [19]
71     2027  Sup                              [16]
72     2033  Sup                              [19]
73     2034  Sup                              [19]
74     2102  Sup                      [17, 18, 19]
75     2103  Sup                          [18, 19]
76     2104  Sup                  [16, 17, 18, 19]
77     2105  Sup           

In [ ]:
# Check if week 20 reminders range from (12,13,14,15,16,17,18,19)

In [45]:
contacts = pd.read_sql_query("select * from registration;", con=engine)

reminders = pd.merge(report.reset_index(), contacts, on=['siteid', 'type'])
reminders

In [39]:
contacts.head()

NameError: name 'contacts' is not defined

In [47]:
reminders = pd.merge(report.reset_index(), contacts, on=['siteid', 'type'])
reminders

NameError: name 'report' is not defined

In [58]:
reminders['number_of_missing_week'] = reminders['weeknum'].map(len)
reminders

siteid type                   weeknum  \
0      201110007  OTP                        []   
1      201110007  OTP                        []   
2      201110009  OTP                        []   
3      201110009  OTP                        []   
4      201110021  OTP  [13, 14, 15, 16, 17, 18]   
5      201110021  OTP  [13, 14, 15, 16, 17, 18]   
6      201110026  OTP  [13, 14, 15, 16, 17, 18]   
7      201110026  OTP  [13, 14, 15, 16, 17, 18]   
8      201110029  OTP  [13, 14, 15, 16, 17, 18]   
9      201110029  OTP  [13, 14, 15, 16, 17, 18]   
10     202110019  OTP                  [14, 18]   
11     202110019  OTP                  [14, 18]   
12     202110021  OTP                      [18]   
13     202110021  OTP                      [18]   
14     202110021  OTP                      [18]   
15     202110021  OTP                      [18]   
16     202110027  OTP  [13, 14, 15, 16, 17, 18]   
17     202110027  OTP  [13, 14, 15, 16, 17, 18]   
18     202110035  OTP                      [18]   
19     202110035  OTP                      [18]   
20     202110035  OTP                      [18]   
21     202110035  OTP                      [18]   
22     202110068  OTP                        []   
23     202110068  OTP                        []   
24     202110068  OTP                        []   
25     202610001   SC                        []   
26     203110002  OTP                        []   
27     203110002  OTP                        []   
28     203110002  OTP                        []   
29     203110037  OTP                        []   
...          ...  ...                       ...   
2034  3609110043  OTP                        []   
2035  3609210040   SC                      [18]   
2036  3609210040   SC                      [18]   
2037  3611110009  OTP                      [18]   
2038  3611110009  OTP                      [18]   
2039  3611110018  OTP          [15, 16, 17, 18]   
2040  3611110018  OTP          [15, 16, 17, 18]   
2041  3611110018  OTP          [15, 16, 17, 18]   
2042  3611110022  OTP                        []   
2043  3611110022  OTP                        []   
2044  3611110022  OTP                        []   
2045  3611110026  OTP      [14, 15, 16, 17, 18]   
2046  3611110026  OTP      [14, 15, 16, 17, 18]   
2047  3611110026  OTP      [14, 15, 16, 17, 18]   
2048  3611110033  OTP                      [18]   
2049  3611110033  OTP                      [18]   
2050  3611210034   SC                        []   
2051  3611210034   SC                        []   
2052  3613110001  OTP                  [17, 18]   
2053  3613110001  OTP                  [17, 18]   
2054  3613110001  OTP                  [17, 18]   
2055  3613110010  OTP                      [18]   
2056  3613110010  OTP                      [18]   
2057  3613110022  OTP                        []   
2058  3613110022  OTP                        []   
2059  3613110044  OTP                        []   
2060  3613110044  OTP                        []   
2061  3613110051  OTP                      [18]   
2062  3613110051  OTP                      [18]   
2063  3613210035   SC  [13, 14, 15, 16, 17, 18]   

                              contact_uuid             urn  \
0     70eaa1cc-40ee-4323-aed3-647767bffcda  +2348134107585   
1     c004920d-9463-4176-a672-ce4332583b9d  +2349021245510   
2     3857d121-cfef-4b64-afb6-74022862f6ea  +2348160018409   
3     1a4b900e-803e-43bb-a786-cf8e60435155  +2348165753101   
4     ecb54d20-74cd-471d-a4a7-0f0208b88bdd  +2348092914506   
5     7a9cdd08-35d3-481e-a2c1-12999890a6dd  +2349091141475   
6     8ffd3195-a53c-4069-b394-ab665a0a64d0  +2348029967848   
7     e890a957-cf10-4da0-b538-8a03a6c7844f  +2348022022110   
8     681f91d1-ca59-4d32-bdd5-0081357bcf54  +2347080871500   
9     ba1f390c-8a0d-4cba-b588-43b6bec664c8  +2349023158231   
10    b679ca25-db75-4137-90e5-8dfbc56bfef2  +2348086762757   
11    bd5385d4-5953-4a65-829d-1ffd25ae3bb9  +2347033992688   
12    2ab2d7c2-b1a5-4cec-857a-a0d06ddaf77

In [59]:
reminders.query('number_of_missing_week > 0')

siteid type                   weeknum  \
4      201110021  OTP  [13, 14, 15, 16, 17, 18]   
5      201110021  OTP  [13, 14, 15, 16, 17, 18]   
6      201110026  OTP  [13, 14, 15, 16, 17, 18]   
7      201110026  OTP  [13, 14, 15, 16, 17, 18]   
8      201110029  OTP  [13, 14, 15, 16, 17, 18]   
9      201110029  OTP  [13, 14, 15, 16, 17, 18]   
10     202110019  OTP                  [14, 18]   
11     202110019  OTP                  [14, 18]   
12     202110021  OTP                      [18]   
13     202110021  OTP                      [18]   
14     202110021  OTP                      [18]   
15     202110021  OTP                      [18]   
16     202110027  OTP  [13, 14, 15, 16, 17, 18]   
17     202110027  OTP  [13, 14, 15, 16, 17, 18]   
18     202110035  OTP                      [18]   
19     202110035  OTP                      [18]   
20     202110035  OTP                      [18]   
21     202110035  OTP                      [18]   
38     203110053  OTP                  [17, 18]   
39     203110053  OTP                  [17, 18]   
42     204110014  OTP                  [17, 18]   
43     204110014  OTP                  [17, 18]   
44     204110014  OTP                  [17, 18]   
45     204110026  OTP                      [18]   
46     204110026  OTP                      [18]   
47     204110029  OTP                      [18]   
48     204110029  OTP                      [18]   
49     204110035  OTP                  [17, 18]   
50     204110035  OTP                  [17, 18]   
51     204110035  OTP                  [17, 18]   
...          ...  ...                       ...   
2017  3607210081   SC                      [18]   
2018  3607310003   SC                  [17, 18]   
2019  3607310003   SC                  [17, 18]   
2020  3607310003   SC                  [17, 18]   
2023  3609110014  OTP                      [18]   
2024  3609110014  OTP                      [18]   
2025  3609110014  OTP                      [18]   
2026  3609110022  OTP                      [18]   
2027  3609110022  OTP                      [18]   
2028  3609110022  OTP                      [18]   
2035  3609210040   SC                      [18]   
2036  3609210040   SC                      [18]   
2037  3611110009  OTP                      [18]   
2038  3611110009  OTP                      [18]   
2039  3611110018  OTP          [15, 16, 17, 18]   
2040  3611110018  OTP          [15, 16, 17, 18]   
2041  3611110018  OTP          [15, 16, 17, 18]   
2045  3611110026  OTP      [14, 15, 16, 17, 18]   
2046  3611110026  OTP      [14, 15, 16, 17, 18]   
2047  3611110026  OTP      [14, 15, 16, 17, 18]   
2048  3611110033  OTP                      [18]   
2049  3611110033  OTP                      [18]   
2052  3613110001  OTP                  [17, 18]   
2053  3613110001  OTP                  [17, 18]   
2054  3613110001  OTP                  [17, 18]   
2055  3613110010  OTP                      [18]   
2056  3613110010  OTP                      [18]   
2061  3613110051  OTP                      [18]   
2062  3613110051  OTP                      [18]   
2063  3613210035   SC  [13, 14, 15, 16, 17, 18]   

                              contact_uuid             urn  \
4     ecb54d20-74cd-471d-a4a7-0f0208b88bdd  +2348092914506   
5     7a9cdd08-35d3-481e-a2c1-12999890a6dd  +2349091141475   
6     8ffd3195-a53c-4069-b394-ab665a0a64d0  +2348029967848   
7     e890a957-cf10-4da0-b538-8a03a6c7844f  +2348022022110   
8     681f91d1-ca59-4d32-bdd5-0081357bcf54  +2347080871500   
9     ba1f390c-8a0d-4cba-b588-43b6bec664c8  +2349023158231   
10    b679ca25-db75-4137-90e5-8dfbc56bfef2  +2348086762757   
11    bd5385d4-5953-4a65-829d-1ffd25ae3bb9  +2347033992688   
12    2ab2d7c2-b1a5-4cec-857a-a0d06ddaf776  +2348103586218   
13    4e09ed3b-3131-4dd0-833d-2f0b6b72e98d  +2348088482226   
14    2a9d3e03-aa86-441f-9e88-d1be411af60b  +2347033046946   
15    bfcecffc-a6ff-481b-b521-905137c52c0d  +2348126658516   
16    d5011ff1-8d59-4733-bb8d-eec43020b7e

In [126]:
set([tuple(sorted(x)) for x in reminders.query('number_of_missing_week > 0').weeknum])

NameError: name 'reminders' is not defined

In [ ]:
# Correct the text of the message if there are no missing program or stock reports

In [29]:
# Step by step view of code to create weekly reminders

# Data cleaning
demo = df.query('since_x_weeks>0')\
        .query('since_x_weeks<=8')\
        .query('siteid>101110001')\


In [30]:
demo = demo.groupby(['siteid', 'type'])['weeknum']
#         .unique()\
#         .map(lambda x: list(sorted(set(range(week - 8, week)) - set(x))))\
#         .to_frame()

demo
# asking for presentation of dataframe, but demo is SeriesGroupBy object

In [31]:
demo.unique()
# PRESENTS unsorted list of weeknumbers of program data
# Only the reports that are confirmed as correct by the reporter are imported

siteid      type
201110007   OTP     [12, 11, 13, 18, 17, 16, 15, 14]
201110009   OTP     [13, 12, 11, 14, 15, 17, 16, 18]
201110021   OTP                             [12, 11]
201110026   OTP                             [11, 12]
201110029   OTP                             [11, 12]
202110019   OTP             [17, 16, 15, 13, 12, 11]
202110021   OTP         [12, 11, 15, 14, 13, 16, 17]
202110027   OTP                             [11, 12]
202110035   OTP         [11, 14, 13, 12, 17, 16, 15]
202110068   OTP     [16, 11, 15, 14, 17, 12, 13, 18]
202610001   SC      [11, 18, 17, 16, 15, 14, 13, 12]
203110002   OTP     [13, 15, 14, 12, 11, 16, 18, 17]
203110037   OTP     [12, 15, 14, 17, 16, 13, 11, 18]
203110038   OTP     [12, 11, 13, 17, 16, 15, 14, 18]
203110043   OTP     [13, 12, 15, 14, 11, 17, 16, 18]
203110053   OTP             [13, 11, 12, 16, 14, 15]
204110006   OTP     [16, 12, 11, 14, 13, 15, 17, 18]
204110014   OTP             [15, 12, 11, 16, 13, 14]
204110026   OTP         [12, 

In [35]:
demo = demo.unique()\
    .map(lambda x: list(sorted(set(range(week - 8, week)) - set(x))))
# ITERATE over each row in series - here (or df)
# CREATE sorted set from current week -8 up to but not including current week
# COMPARE this sorted set to the set of received report weeknumbers to 
# PRODUCE list of missing program reports for site in past 8 weeks

demo

siteid      type
201110007   OTP                               []
201110009   OTP                               []
201110021   OTP         [13, 14, 15, 16, 17, 18]
201110026   OTP         [13, 14, 15, 16, 17, 18]
201110029   OTP         [13, 14, 15, 16, 17, 18]
202110019   OTP                         [14, 18]
202110021   OTP                             [18]
202110027   OTP         [13, 14, 15, 16, 17, 18]
202110035   OTP                             [18]
202110068   OTP                               []
202610001   SC                                []
203110002   OTP                               []
203110037   OTP                               []
203110038   OTP                               []
203110043   OTP                               []
203110053   OTP                         [17, 18]
204110006   OTP                               []
204110014   OTP                         [17, 18]
204110026   OTP                             [18]
204110029   OTP                             [18]
204

In [39]:
from temba_client.v2 import TembaClient

client = TembaClient('rapidpro.io', open('token').read().strip())

In [40]:
client.create_broadcast?

In [52]:
def send_reminders(row_in_df):
    # client.create_broadcast(row_in_df['message'], contacts=[row_in_df['contact_uuid']])
    print "client.create_broadcast('%s', contacts=%s)" % (row_in_df['message'], [row_in_df['contact_uuid']])
    
reminders_sites.apply(send_reminders, axis=1)


client.create_broadcast('Dear Gracegidado from DONG  HEALTH CLINIC. Reminder to send PROGRAM reports for weeks 19 and STOCK reports for weeks 19.', contacts=[u'70eaa1cc-40ee-4323-aed3-647767bffcda'])
client.create_broadcast('Dear Assurance David from DONG  HEALTH CLINIC. Reminder to send PROGRAM reports for weeks 19 and STOCK reports for weeks 19.', contacts=[u'c004920d-9463-4176-a672-ce4332583b9d'])
client.create_broadcast('Dear Elcy Jemuel from KPASHAM MAT. CLINIC. Reminder to send PROGRAM reports for weeks 13, 14, 15, 16, 17, 18, 19 and STOCK reports for weeks 13, 14, 15, 16, 17, 18, 19.', contacts=[u'ecb54d20-74cd-471d-a4a7-0f0208b88bdd'])
client.create_broadcast('Dear Regina Nathan from KPASHAM MAT. CLINIC. Reminder to send PROGRAM reports for weeks 13, 14, 15, 16, 17, 18, 19 and STOCK reports for weeks 13, 14, 15, 16, 17, 18, 19.', contacts=[u'7a9cdd08-35d3-481e-a2c1-12999890a6dd'])
client.create_broadcast('Dear Mary Chindo from BILLE  MATERNITY CLINIC. Reminder to send PROGRAM r

0       None
1       None
2       None
3       None
4       None
5       None
6       None
7       None
8       None
9       None
10      None
11      None
12      None
13      None
14      None
15      None
16      None
17      None
18      None
19      None
20      None
21      None
22      None
23      None
24      None
25      None
26      None
27      None
28      None
29      None
30      None
31      None
32      None
33      None
34      None
35      None
36      None
37      None
38      None
39      None
40      None
41      None
42      None
43      None
44      None
45      None
46      None
47      None
48      None
49      None
50      None
51      None
52      None
53      None
54      None
55      None
56      None
57      None
58      None
59      None
60      None
61      None
62      None
63      None
64      None
65      None
66      None
67      None
68      None
69      None
70      None
71      None
72      None
73      None
74      None
75      None
76      None

In [41]:
# API call to send message to Assaye
client.create_broadcast("Now we can spam you all day and night", contacts=["f4edf16b-f936-4ff3-b6aa-5b3ef15d948d"])

In [59]:
# client.create_broadcast("Now we can spam you all day and night", contacts=["f4edf16b-f936-4ff3-b6aa-5b3ef15d948d"])
client.update_contact("00771990-6cda-4987-b329-90eda5b43683", fields={'post': 'not here anymore'})



In [64]:
field = next(client.get_fields().iterfetches(retry_on_rate_exceed=True))[0]

In [67]:
field.key

u'sno9num'

In [68]:
# from the list in lists that API formats data in, remove one layer of the list
all_fields = reduce(lambda x, y: x+y, [x for x in client.get_fields().iterfetches(retry_on_rate_exceed=True)], [])

In [70]:
[x.key for x in all_fields]

[u'sno9num',
 u'sno9name',
 u'sno9mail',
 u'sno8num',
 u'sno8name',
 u'sno8mail',
 u'sno7num',
 u'sno7name',
 u'sno7mail',
 u'sno6num',
 u'sno6name',
 u'sno6mail',
 u'sno5num',
 u'sno5name',
 u'sno5mail',
 u'sno4num',
 u'sno4name',
 u'sno4mail',
 u'sno18num',
 u'sno18name',
 u'sno18mail',
 u'sno17num',
 u'sno17name',
 u'sno17mail',
 u'sno16num',
 u'sno16name',
 u'sno16mail',
 u'sno15num',
 u'sno15name',
 u'sno15mail',
 u'sno14num',
 u'sno14name',
 u'sno14mail',
 u'sno13num',
 u'sno13name',
 u'sno13mail',
 u'sno12num',
 u'sno12name',
 u'sno12mail',
 u'sno11num',
 u'sno11name',
 u'sno11mail',
 u'sno10num',
 u'sno10name',
 u'sno10mail',
 u'lga5num',
 u'lga5name',
 u'lga5mail',
 u'lga4num',
 u'lga4name',
 u'lga4mail',
 u'lga3num',
 u'lga3name',
 u'lga3mail',
 u'lga2num',
 u'lga2name',
 u'lga2mail',
 u'lga1mail',
 u'lga1name',
 u'lga1num',
 u'sno3mail',
 u'sno3num',
 u'sno3name',
 u'sno2mail',
 u'sno2num',
 u'sno2name',
 u'sno1mail',
 u'sno1num',
 u'sno1name',
 u'mnps',
 u'state',
 u'lga',


In [6]:
# Compare weekly reminders calculation of missing week reports

import pandas as pd

pandf = pd.ExcelFile('/home/robert/PycharmProjects/IMAM/Weekly Reminders.xlsx').parse('Sheet1')
xlsdf = pd.ExcelFile('/home/robert/PycharmProjects/IMAM/Weekly Reminders.xlsx').parse('Sheet2')



In [18]:
pandf.head()
#xlsdf.head()

state_num_x  lga_num_x     siteid type missing_program missing_stock  \
0            2        201  201110007  OTP           19 20         19 20   
1            2        201  201110007  OTP           19 20         19 20   
2            2        201  201110021  OTP        18 19 20      18 19 20   
3            2        201  201110021  OTP        18 19 20      18 19 20   
4            2        202  202110019  OTP     14 18 19 20   14 18 19 20   

               name                 sitename            urn  Unnamed: 9  \
0      Gracegidado.      DONG  HEALTH CLINIC  2348134107585         NaN   
1  Assurance David.      DONG  HEALTH CLINIC  2349021245510         NaN   
2      Elcy Jemuel.      KPASHAM MAT. CLINIC  2348092914506         NaN   
3    Regina Nathan.      KPASHAM MAT. CLINIC  2349091141475         NaN   
4      Ahmed Aminu.  FUFORE MATERNITY CENTRE  2348086762757         NaN   

               first_seen               last_seen                      post  \
0 2016-10-25 09:10:31.153 2017-05-17 16:21:15.937  Community Health Officer   
1 2016-10-25 09:05:47.222 2017-05-17 16:21:13.853  Community Health Officer   
2 2016-10-25 09:20:54.251 2017-05-18 07:21:29.519  Community Health Officer   
3 2016-10-25 09:13:06.611 2017-05-17 16:21:27.299  Community Health Officer   
4 2016-10-25 09:21:41.934 2017-05-17 16:21:40.636  Community Health Officer   

                       mail  Unnamed: 14  \
0                       NaN          NaN   
1                       NaN          NaN   
2                       NaN          NaN   
3                       NaN          NaN   
4  ahmedaminu2044@yahoo.com          NaN   

                                             message  
0  Dear Gracegidado from DONG  HEALTH CLINIC. Rem...  
1  Dear Assurance David from DONG  HEALTH CLINIC....  
2  Dear Elcy Jemuel from KPASHAM MAT. CLINIC. Rem...  
3  Dear Regina Nathan from KPASHAM MAT. CLINIC. R...  
4  Dear Ahmed Aminu from FUFORE MATERNITY CENTRE....

In [26]:
print len(pandf)
print len(xlsdf)

1339
1530


In [19]:
pd.merge?


In [15]:
#Strip out [] and commas from missing_stock and missing_program
#pandf = pandf.missing_program.map(lambda x: strip)

pandf['missing_program'] = pandf['missing_program'].str.replace('[', '').str.replace(']', '').str.replace(',', '')
pandf['missing_stock'] = pandf['missing_stock'].str.replace('[', '').str.replace(']', '').str.replace(',', '')

In [30]:
merged = pd.merge(right = pandf, left = xlsdf, right_on ='urn', left_on = 'Phone', how = 'outer')
merged

Phone                      Name   state     lga  \
0     2.348063e+12         Ahmed Usman Dige.   Gombe   Dukku   
1     2.349034e+12          Mohammed Yahaya.   Gombe   Dukku   
2     2.348137e+12             Dahiru Siddi.   Gombe   Dukku   
3     2.348124e+12       Zainab Muhd Adamu .   Gombe   Gombe   
4     2.348068e+12         Sani Adamu Jauro.   Gombe   Gombe   
5     2.348178e+12                    72221.   Gombe   Gombe   
6     2.347069e+12      Zainab Umar Chiroma.   Gombe   Gombe   
7     2.348036e+12           Williams Attah.   Gombe   Gombe   
8     2.348062e+12      Basiratu Abdulsalam.   Gombe   Gombe   
9     2.347034e+12      Kanadi Hassan Ahmed.   Gombe   Gombe   
10    2.348034e+12         Dahiru Abdullahi.   Gombe   Gombe   
11    2.348036e+12            Hadiza Jibrin.   Gombe   Gombe   
12    2.349030e+12             Hafsat Usman.   Gombe   Gombe   
13    2.347069e+12      Abubakar Umar Usman.   Gombe  Nafada   
14    2.348083e+12       Moh'D M.Moh'D Sam .   Gombe  Nafada   
15    2.347039e+12     Ibrahi Mohammed Biri.   Gombe  Nafada   
16    2.348082e+12  Mohammed Sulaiman Barwo.   Gombe  Nafada   
17    2.348087e+12        Abubakar Mohammad.   Gombe  Nafada   
18    2.348088e+12            Ahidu Jungudo.   Gombe  Nafada   
19    2.348080e+12            Ahidu Jungudo.   Gombe  Nafada   
20    2.347086e+12                   Ahmed .   Gombe  Nafada   
21    2.348161e+12          Maijidda Yakubu.  Jigawa  Babura   
22    2.348067e+12               Abdu Ahmed.  Jigawa  Babura   
23    2.348032e+12               Shehu Abdu.  Jigawa  Babura   
24    2.348093e+12    Abubakar Salisu Kanya.  Jigawa  Babura   
25    2.349094e+12               Shehu Abdu.  Jigawa  Babura   
26    2.348039e+12    Abubakar Salisu Kanya.  Jigawa  Babura   
27    2.348167e+12               Sadiq Sadi.  Jigawa  Babura   
28    2.348066e+12           Alyasau Salisu.  Jigawa  Babura   
29    2.348036e+12    Albusari Basiru Musa .  Jigawa  Babura   
...            ...                       ...     ...     ...   
1551           NaN                       NaN     NaN     NaN   
1552           NaN                       NaN     NaN     NaN   
1553           NaN                       NaN     NaN     NaN   
1554           NaN                       NaN     NaN     NaN   
1555           NaN                       NaN     NaN     NaN   
1556           NaN                       NaN     NaN     NaN   
1557           NaN                       NaN     NaN     NaN   
1558           NaN                       NaN     NaN     NaN   
1559           NaN                       NaN     NaN     NaN   
1560           NaN                       NaN     NaN     NaN   
1561           NaN                       NaN     NaN     NaN   
1562           NaN                       NaN     NaN     NaN   
1563           NaN                       NaN     NaN     NaN   
1564           NaN                       NaN     NaN     NaN   
1565           NaN                       NaN     NaN     NaN   
1566           NaN                       NaN     NaN     NaN   
1567           NaN                       NaN     NaN     NaN   
1568           NaN                       NaN     NaN     NaN   
1569           NaN                       NaN     NaN     NaN   
1570           NaN                       NaN     NaN     NaN   
1571           NaN                       NaN     NaN     NaN   
1572           NaN                       NaN     NaN     NaN   
1573           NaN                       NaN     NaN     NaN   
1574           NaN                       NaN     NaN     NaN   
1575           NaN                       NaN     NaN     NaN   
1576           NaN                       NaN     NaN     NaN   
1577           NaN                       NaN     NaN     NaN   
1578           NaN                       NaN     NaN     NaN   
1579           NaN                       NaN     NaN     NaN   
1580           NaN                       NaN     NaN     NaN   

                      SiteName        SiteID

In [45]:
def compare(row):
    print repr(row['StoMiss']), repr(row['missing_stock']), (row['StoMiss'].strip() == row['missing_stock'])
    
merged.apply(compare, axis=1)

u' 20 ' u'20' True
u' 20 ' u'20' True
u' 20 ' u'20' True
u' 19 20 ' u'19 20' True
u' 19 20 ' u'19 20' True
u' 19 20 ' u'19 20' True
u' 19 20 ' u'19 20' True
u' 16 17 18 19 20 ' u'16 17 18 19 20' True
u' 16 17 18 19 20 ' u'16 17 18 19 20' True
u' 16 17 18 19 20 ' u'16 17 18 19 20' True
u' 16 17 18 19 20 ' u'16 17 18 19 20' True
u' 18 19 20 ' u'18 19 20' True
u' 18 19 20 ' u'18 19 20' True
u' 15 16 17 18 19 20 ' u'15 16 17 18 19 20' True
u' 15 16 17 18 19 20 ' u'15 16 17 18 19 20' True
u' 19 20 ' u'19 20' True
u' 15 16 17 18 19 20 ' u'14 15 16 17 18 19 20' False
u' 15 16 17 18 19 20 ' u'14 15 16 17 18 19 20' False
u' 13 14 15 16 17 18 19 20 ' nan False
u' 18 19 20 ' u'18 19 20' True
u' 13 14 15 16 17 18 19 20 ' nan False
u' 19 20 ' u'18 19 20' False
u' 19 20 ' u'18 19 20' False
u' 20 ' u'20' True
u' 20 ' u'20' True
u' 20 ' u'20' True
u' 20 ' u'20' True
u' 20 ' u'20' True
u' 20 ' u'20' True
u' 20 ' u'20' True
u' 19 20 ' u'19 20' True
u' 19 20 ' u'19 20' True
u' 18 ' u'18' True
u' 18 ' u'1

AttributeError: ("'float' object has no attribute 'strip'", u'occurred at index 1530')

In [51]:
(merged['StoMiss'].map(lambda x: x.strip() if x == x else x) == merged['missing_stock'].map(lambda x: x.strip() if x == x else x)).value_counts()

True     1170
False     411
dtype: int64

In [52]:
(merged['ProMiss'].map(lambda x: x.strip() if x == x else x) == merged['missing_program'].map(lambda x: x.strip() if x == x else x)).value_counts()

True     1188
False     393
dtype: int64

In [53]:
merged['stodiff'] = merged['StoMiss'].map(lambda x: x.strip() if x == x else x) == merged['missing_stock'].map(lambda x: x.strip() if x == x else x)
merged['prodiff'] = merged['ProMiss'].map(lambda x: x.strip() if x == x else x) == merged['missing_program'].map(lambda x: x.strip() if x == x else x)

In [56]:
merged['stomiss_len'] = merged['StoMiss'].map(lambda x: len(x.strip().split(' ')) if x == x else 0)
merged['promiss_len'] = merged['ProMiss'].map(lambda x: len(x.strip().split(' ')) if x == x else 0)

In [58]:
merged['stomiss_len'].value_counts()

1    506
2    285
8    240
3    221
4    133
5     51
0     51
7     50
6     44
Name: stomiss_len, dtype: int64

In [59]:
merged['promiss_len'].value_counts()

1    538
2    272
3    243
8    228
4    103
5     56
0     51
7     48
6     42
Name: promiss_len, dtype: int64

In [64]:
len(merged.query('stodiff == False | prodiff == False')) - 222

274

In [65]:
diff = merged.query('not (missing_stock != missing_stock & promiss_len == 8 & stomiss_len == 8)').query('stodiff == False | prodiff == False')
diff

Phone                        Name    state           lga  \
13    2.347069e+12        Abubakar Umar Usman.    Gombe        Nafada   
14    2.348083e+12         Moh'D M.Moh'D Sam .    Gombe        Nafada   
16    2.348082e+12    Mohammed Sulaiman Barwo.    Gombe        Nafada   
17    2.348087e+12          Abubakar Mohammad.    Gombe        Nafada   
21    2.348161e+12            Maijidda Yakubu.   Jigawa        Babura   
22    2.348067e+12                 Abdu Ahmed.   Jigawa        Babura   
37    2.348039e+12                Hadiza Nuhu.   Jigawa   Birnin Kudu   
38    2.348037e+12             Musa Abdu Sara.   Jigawa   Birnin Kudu   
59    2.348133e+12            Muhammad Haruna.   Jigawa          Guri   
60    2.347030e+12               Mohammed Ado.   Jigawa          Guri   
65    2.348135e+12          Aisha Muhd Askira.   Jigawa       Hadejia   
66    2.348068e+12               Saleh A Umar.   Jigawa       Hadejia   
75    2.348061e+12       Zahraddeen Abdullahi.   Jigawa         Jahun   
76    2.347031e+12                  Yau Maina.   Jigawa         Jahun   
81    2.347034e+12              Suleiman Muhd.   Jigawa       Kaugama   
82    2.348064e+12                 Garba Sani.   Jigawa       Kaugama   
128   2.348024e+12        Baraatu Ahmad Dikko.   Kaduna  Birnin Gwari   
138   2.348087e+12  Maxwell Chidozie Maduwuba.   Kaduna        Kachia   
139   2.348063e+12  Maduwuba Maxwell Chidozie.   Kaduna        Kachia   
140   2.348031e+12  Maxwell Chidozie Maduwuba.   Kaduna        Kachia   
168   2.348067e+12               Hamisu Aliyu.     Kano         Bichi   
169   2.347061e+12        Tasi'U Ibrahim Ya'U.     Kano         Bichi   
206   2.348164e+12            Sani Ado Indabo.     Kano         Wudil   
207   2.348070e+12         Kabiru Bala Madaki.     Kano         Wudil   
225   2.347034e+12                Lawal Kanta.  Katsina         Baure   
226   2.348065e+12                Lawal Kanta.  Katsina         Baure   
227   2.348063e+12                Aminu Adamu.  Katsina         Baure   
228   2.348061e+12              Hassan Yakubu.  Katsina         Baure   
229   2.348038e+12                 Ayubayusuf.  Katsina         Baure   
230   2.349079e+12           Muntari Zubairu .  Katsina         Baure   
...            ...                         ...      ...           ...   
1551           NaN                         NaN      NaN           NaN   
1552           NaN                         NaN      NaN           NaN   
1553           NaN                         NaN      NaN           NaN   
1554           NaN                         NaN      NaN           NaN   
1555           NaN                         NaN      NaN           NaN   
1556           NaN                         NaN      NaN           NaN   
1557           NaN                         NaN      NaN           NaN   
1558           NaN                         NaN      NaN           NaN   
1559           NaN                         NaN      NaN           NaN   
1560           NaN                         NaN      NaN           NaN   
1561           NaN                         NaN      NaN           NaN   
1562           NaN                         NaN      NaN           NaN   
1563           NaN                         NaN      NaN           NaN   
1564           NaN                         NaN      NaN           NaN   
1565           NaN                         NaN      NaN           NaN   
1566           NaN                         NaN      NaN           NaN   
1567           NaN                         NaN      NaN           NaN   
1568           NaN                         NaN      NaN           NaN   
1569           NaN                         NaN      NaN           NaN   
1570           NaN                         NaN      NaN           NaN   
1571           NaN                         NaN      NaN           NaN   
1572           NaN                         NaN      NaN           NaN   
1573           NaN                         NaN      NaN           NaN  

In [68]:
diff['stomiss_set'] = diff['StoMiss'].map(lambda x: set(x.strip().split(' ') if x == x else set()))
diff['missing_stock_set'] = diff['missing_stock'].map(lambda x: set(x.strip().split(' ') if x == x else set()))

In [76]:
(diff['stomiss_set'] - diff['missing_stock_set']).map(lambda x: str(list(sorted(x)))).value_counts()


[]                                                          228
[u'13', u'14', u'15', u'16', u'17', u'18', u'19', u'20']     18
[u'20']                                                      11
[u'19']                                                       4
[u'14', u'15', u'16']                                         3
[u'13', u'14', u'15', u'16', u'17', u'19', u'20']             2
[u'17']                                                       2
[u'']                                                         2
[u'13', u'15', u'16', u'17', u'18', u'19', u'20']             2
[u'19', u'20']                                                1
[u'18']                                                       1
dtype: int64

In [77]:
(diff['missing_stock_set'] - diff['stomiss_set']).map(lambda x: str(list(sorted(x)))).value_counts()

[]                                                   129
[u'13']                                               18
[u'14']                                               16
[u'17']                                               16
[u'16']                                               15
[u'19']                                               14
[u'18']                                               13
[u'15']                                               12
[u'20']                                               12
[u'']                                                  8
[u'19', u'20']                                         3
[u'18', u'19']                                         2
[u'18', u'19', u'20']                                  2
[u'13', u'14']                                         2
[u'17', u'20']                                         2
[u'14', u'15', u'16', u'17', u'18', u'19', u'20']      2
[u'14', u'15', u'16', u'17']                           2
[u'15', u'16']                 

In [ ]:
# Create sets and do set comparison 
demo = demo.unique()\
    .map(lambda x: list(sorted(set(range(week - 8, week)) - set(x))))